In [4]:
import requests
import pandas as pd
import numpy as np
import time
import json
from bs4 import BeautifulSoup
from sklearn.neighbors import KNeighborsClassifier
import matplotlib.pyplot as plt
import re

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
import time

from sklearn.model_selection import train_test_split, cross_val_score

from psaw import PushshiftAPI

In [110]:
# for later usage

import datetime as dt
def get_date(created):
    return dt.datetime.fromtimestamp(created)

In [5]:
# there are 10 pages on each of the infinite scrolling sephora pages, so here is my loop

loop_list = []

for i in range(1,11):
    URL_loop = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page="+str(i)+"&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
    res_loop = requests.get(URL_loop, headers = {'User-agent': 'Emma York'})
    html_loop = res_loop.text
    loop_list.append(BeautifulSoup(html_loop, 'lxml'))
    print(i)

1
2
3
4
5
6
7
8
9
10


In [6]:
skin_list = []

for i in range(1,11):
    URL_skin = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=70548926928512793&sg=1&pg=res18101616128655390947062&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=" +str(i)+ "&categoryid=cat150006&PrimaryCategoryID=&ccb=Sephora.certona&ur=https%3A%2F%2Fwww.sephora.com%2Fnew-skin-care-products&plk=&rf=https%3A%2F%2Fwww.sephora.com%2Fnew-beauty-products"
    res_skin = requests.get(URL_skin, headers = {'User-agent': 'Emma York'})
    html_skin = res_skin.text
    skin_list.append(BeautifulSoup(html_skin, 'lxml'))
    print(i)

1
2
3
4
5
6
7
8
9
10


In [7]:
best_skin_list = []

for i in range(1,11):
    URL_best_skin = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=70548926928512793&sg=1&pg=res18101617841602331337186&vr=5.5x&bx=true&sc=content2_rr&ev=&ei=&no=20&page=" +str(i)+ "&categoryid=cat150006&PrimaryCategoryID=&ccb=Sephora.certona&ur=https%3A%2F%2Fwww.sephora.com%2Fbest-selling-skin-care&plk=&rf=https%3A%2F%2Fwww.sephora.com%2Fbest-selling-skin-care"
    res_best_skin = requests.get(URL_best_skin, headers = {'User-agent': 'Emma York'})
    html_best_skin = res_best_skin.text
    best_skin_list.append(BeautifulSoup(html_best_skin, 'lxml'))
    print(i)

1
2
3
4
5
6
7
8
9
10


In [8]:
best_list = []

for i in range(1,11):
    URL_best = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=70548926928512793&sg=1&pg=res18101617412752014209901&vr=5.5x&bx=true&sc=content2_rr&ev=&ei=&no=20&page=" +str(i)+ "&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https%3A%2F%2Fwww.sephora.com%2Fbeauty-best-sellers%3FmediaId%3D14300062&plk=&rf=https%3A%2F%2Fwww.sephora.com%2Fbest-selling-skin-care"
    res_best = requests.get(URL_best, headers = {'User-agent': 'Emma York'})
    html_best = res_best.text
    best_list.append(BeautifulSoup(html_best, 'lxml'))
    print(i)

1
2
3
4
5
6
7
8
9
10


In [9]:
# # new skincare list 

skin_brand_name = re.findall('(?<=brand_name":").*?(?=")', str(skin_list))
skin_product_name = re.findall('(?<=display_name":").*?(?=")', str(skin_list))

# best skincare list

best_skin_brand_name = re.findall('(?<=brand_name":").*?(?=")', str(best_skin_list))
best_skin_product_name = re.findall('(?<=display_name":").*?(?=")', str(best_skin_list))

# new generict products

brand_name = re.findall('(?<=brand_name":").*?(?=")', str(loop_list))
product_name = re.findall('(?<=display_name":").*?(?=")', str(loop_list))

# best generic products

best_brand_name = re.findall('(?<=brand_name":").*?(?=")', str(best_list))
best_product_name = re.findall('(?<=display_name":").*?(?=")', str(best_list))

In [13]:
# combining the brand name and product name

skincare_list = list(map(lambda x, y: x+ ' ' +y, skin_brand_name, skin_product_name))
best_skincare_list = list(map(lambda x, y: x+ ' ' +y, best_skin_brand_name, best_skin_product_name))

generic_list = list(map(lambda x, y: x+ ' ' +y, brand_name, product_name))
best_generic_list = list(map(lambda x, y: x+ ' ' +y, best_brand_name, best_product_name))

In [248]:
len(set(skincare_list))

200

In [14]:
# to clean out those lists

def list_cleaner(dirty_list):
    
    dirty_list = [i.lower() for i in dirty_list]
    dirty_list = [i.replace("™", "").replace("®", "").replace("&amp;", "&") for i in dirty_list]
    
    return dirty_list

In [15]:
# using my function!

skincare_list = list_cleaner(skincare_list)
best_skincare_list = list_cleaner(best_skincare_list)

generic_list = list_cleaner(generic_list)
best_generic_list = list_cleaner(best_generic_list)

In [16]:
skincare_list

['dr. jart+ mask heroes face savers',
 'moon juice beauty shroom vegan collagen protection',
 'moon juice beauty shroom exfoliating acid potion',
 'sephora collection face mask magic',
 'laneige kiss and make up set',
 'drunk elephant agent ellie day kit',
 'olehenriksen glow cycle retin-alt power serum',
 'welleco the super elixir',
 'la mer merry little miracles',
 'drunk elephant inspector drunk night kit',
 'sol de janeiro bum bum carnaval extravaganza',
 'tatcha skincare for makeup lovers obento box',
 'fresh sugar jetsetter',
 'olehenriksen glow brightly - radiance-boosting super set',
 'farmacy honeymoon glow aha resurfacing night serum with echinacea greenenvy',
 'drunk elephant the big reveal kit',
 'herbivore jade facial roller',
 'summer fridays overtime mask',
 'fresh sky high-dration',
 'sunday riley good genes holiday kit',
 'fresh destination sugar',
 'algenist secrets of algae kit',
 'peter thomas roth mask frenzy',
 'olehenriksen goodnight glow retin-alt sleeping crème

In [5]:
api = PushshiftAPI()

In [ ]:
fri = api.search_comments(q = "")

In [6]:
fri = api.search_comments(q = 'Sephora', 
                              aggs = 'subreddit',
                              fields = ['doc_count', 'key', 'created_utc'],
                              filter = ['created_utc'],
                              sort_type = 'created_utc',
                              size = 0)

In [8]:
next(fri)

{'subreddit': [{'doc_count': 148501, 'key': 'MakeupAddiction'},
  {'doc_count': 19891, 'key': 'muacjdiscussion'},
  {'doc_count': 13604, 'key': 'MakeupRehab'},
  {'doc_count': 13049, 'key': 'SkincareAddiction'},
  {'doc_count': 10241, 'key': 'makeupexchange'},
  {'doc_count': 9323, 'key': 'AsianBeauty'},
  {'doc_count': 8227, 'key': 'BeautyBoxes'},
  {'doc_count': 7903, 'key': 'RandomActsofMakeup'},
  {'doc_count': 6143, 'key': 'MakeupAddicts'},
  {'doc_count': 5301, 'key': 'AskReddit'},
  {'doc_count': 4721, 'key': 'Makeup'},
  {'doc_count': 4454, 'key': 'AustralianMakeup'},
  {'doc_count': 4207, 'key': 'BeautyGuruChatter'},
  {'doc_count': 3880, 'key': 'MakeupAddictionCanada'},
  {'doc_count': 3066, 'key': 'AskWomen'},
  {'doc_count': 2975, 'key': 'MUAontheCheap'},
  {'doc_count': 2790, 'key': 'fragrance'},
  {'doc_count': 2752, 'key': 'muacirclejerk'},
  {'doc_count': 2429, 'key': 'femalefashionadvice'},
  {'doc_count': 2384, 'key': 'RedditLaqueristas'},
  {'doc_count': 1594, 'key':

In [19]:
# utc_code = re.findall('(?<=created_utc=).*?(?=,)', str(gent))
# keys = re.findall("(?<='key': ').*?(?=')", str(gent))
# doc_count = re.findall("(?<='doc_count': ).*?(?=, 'key')", str(gent))

In [20]:
#re.findall("(?<='doc_count': ).*?(?=, 'key')", str(gent))

In [21]:
# ## THIS IS THE RIGHT ONE PLEASE FOR THE LOVE OF GOD DO NOT DELETE THIS ONE

# data_dict_test = {}
# for i in range(0,200):
#     new_gen = api.search_comments(q = skin_thing[i], 
#                                   subreddit = 'SkincareAddiction', 
#                                   sort = 'asc', 
#                                   fields = ['created_utc', 'score'], 
#                                   size = 10)
#     data_dict_test[skin_thing[i]] = list(new_gen)
#     print(i)

In [22]:
# # here I will pull all the times the subreddit SkincareAddiction has mentioned the products/brands
# # on the Sephora 2018 new item's list

# new_text_list = [skin_thing, skin_brand_thing, generic_product_thing, generic_brand_thing]
# data_dict_new = {}

# for j in new_text_list:
#     for i in range(0,200):
#         new_gen = api.search_comments(q = j[i], 
#                                   subreddit = 'SkincareAddiction', 
#                                   sort = 'asc', 
#                                   fields = ['created_utc', 'score'], 
#                                   size = 10)
#         data_dict_new[j[i]] = list(new_gen)
#         print(i)

In [23]:
# comparing my list to sephora

new_list = [skincare_list, generic_list]
data_new = {}

for j in new_list:
    for i in range(0,200):
        new_gen = api.search_comments(q = j[i], 
                                  subreddit = 'SkincareAddiction', 
                                  sort = 'asc', 
                                  fields = ['created_utc', 'score'], 
                                  size = 10)
        data_new[j[i]] = list(new_gen)
        print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104


In [24]:
utc_combo_list = []
score_combo_list = []

for i in list(data_new.keys()):
    if data_new[i] == []:
        utc_combo_list.append('N/A')
        score_combo_list.append('N/A')
    else:
        d = get_date(data_new[i][0].created_utc)
        s = data_new[i][0].score
        utc_combo_list.append(d)
        score_combo_list.append(s)

In [27]:
# tucker did this

allure_2017 = ['Glossier Milky Jelly Cleanser',
 'Skinfix Foaming Clay Cleanser',
 'Rodan + Fields Soothe Gentle Cream Wash',
 'Mustela Facial Cleansing Wipes',
 'Julep Love Your Bare Face Detoxifying Cleansing Stick',
 'Fresh Rose Deep Hydration Facial Toner',
 'H2O+ AquaDefense Shielding Matcha Facial Essence',
 'Caudalie Vine Activ Overnight Detox Night Oil',
 'Aveeno Absolutely Ageless Intensive Renewal Serum',
 'RoC Retinol Correxion Deep Wrinkle Daily Moisturizer',
 'No7 Lift & Luminate Triple Action Serum',
 'Olay Luminous Miracle Boost Concentrate',
 'L’Oréal Paris Hydra Genius Daily Liquid Care Moisturizer',
 'Estée Lauder DayWear Matte Oil-Control Antioxidant Moisture Gel Creme',
 'Garnier SkinActive Moisture Bomb the Antioxidant Super Moisturizer',
 'StriVectin Retinol Eye Cream',
 'First Aid Beauty Eye Duty Triple Remedy AM Gel Cream',
 'Elizabeth Arden Advanced Ceramide Capsules Daily Youth Restoring Eye Serum',
 'Aveda Tulasara Wedding Masque Eye Overnight',
 'Clinique Pep-Start Eye Cream',
 'E.L.F. Gentle Peeling Exfoliant',
 'Philosophy Purity Made Simple Pore Extractor Exfoliating Clay Mask',
 'Dr. Jart+ Rubber Mask Bright Lover',
 'Garnier SkinActive Moisture Bomb the Super Hydrating Sheet Mask',
 'Shiseido Beneficiance Retinol Eye Mask',
 'Laneige Water Sleeping Mask',
 'La Roche-Posay Anthelios Clear Skin Dry Touch Sunscreen SPF 60',
 'SkinCeuticals Physical Fusion UV Defense SPF 50',
 'Skinfix Facial Exfoliating Pads',
 'Differin Gel',
 'Kiehl’s Breakout Control Targeted Acne Spot Treatment',
 'La Roche-Posay Effaclar Dermatological 3-Step Acne System',
 'L’Oréal Paris Extraordinary Clay Shampoo',
 'Pantene Pro-V Daily Moisture Renewal Shampoo',
 ' Virtue Recovery Shampoo',
 ' Schwarzkopf Gliss Ultimate Shampoo',
 'SheaMoisture Smooth & Tame Shampoo',
 'Inoar Divine Curls Shampoo',
 'Dove DermaCare Scalp Dryness & Itch Relief Shampoo',
 'As I Am Coconut CoWash Cleansing Conditioner',
 'John Frieda Frizz Ease 10 Day Tamer Pre-Shower Treatment',
 'Redken Extreme Mega Mask',
 'Briogeo Scalp Revival Charcoal + Tea Tree Scalp Treatment',
 'OGX Fade-Defying + Orchid Oil Color Protect Oil',
 "Rogaine Women's 5% Minoxidil Foam",
 'Sexy Hair Big Sexy Hair Powder Play Lite',
 'Alterna Caviar CC Cream',
 'Color Wow Dream Coat Supernatural Spray',
 'Nexxus City Shield DD Créme',
 'Curls Blueberry Bliss Curl Control Jelly',
 'IGK Rich Kid Coconut Oil Gel',
 'Ouai Wave Spray',
 "Not Your Mother's Coconut Milk & African Marula Tree Oil High Moisture Smoothing Cream",
 'Creme of Nature with Argan Oil Perfect Edges Extra Hold',
 'Carol’s Daughter Pracaxi Nectar Curl Twisting Custard',
 'Oribe Free Styler Working Hairspray',
 'Paul Mitchell Awapuhi Wild Ginger Texturizing Sea Spray',
 'Garnier Fructis Moisture Lock 10-in-1 Rescue Leave-In Spray',
 'Flawless by Gabrielle Union Shine Spray',
 'Wella Professionals Oil Reflections Luminous Smoothing Oil',
 'Hask Charcoal Purifying Dry Shampoo',
 'eSalon Made for You Custom Hair Color',
 'DpHue Root Touch-Up Kit',
 'Color Wow Root Cover Up',
 'Clairol Color Crave Hair Makeup',
 'John Frieda Clear Shine Luminous Glaze',
 "Paula's Choice Resist Smoothing Primer Serum",
 'CoverGirl Vitalist Healthy Elixir Foundation',
 'Dior Diorskin Forever Fluid Foundation',
 'Shiseido Synchro Skin Glow Luminizing Fluid Foundation',
 'Burt’s Bees Mattifying Powder Foundation',
 'BareMinerals Complexion Rescue Tinted Hydrating Gel Cream',
 'Neutrogena Hydro Boost Hydrating Tint',
 'Flower Beauty Flower Pots Powder Blush',
 'Tom Ford Shade and Illuminate Cheeks Blush',
 'Milk Makeup Holographic Stick in Mars',
 'Make Up For Ever Pro Light Fusion',
 'KKW Beauty Crème Contour & Highlight Kit',
 'Laura Mercier Candleglow Sheer Perfecting Powder',
 'Kat Von D Lock-It Brightening Powder',
 'Lancôme Teint Idole Ultra Wear Camouflage Concealer',
 'Nars Soft Matte Complete Concealer',
 'Tan-Luxe The Face Illuminating Self-Tan Drops',
 'Marc Jacobs Beauty Omega Bronze Perfect Tan Bronzer',
 'L’Oréal Paris Sublime Bronze Summer Express Wash-Off Face Bronzer Cream',
 'Pat McGrath Labs Lust MatteTrance Lipstick in Elson',
 'Gucci Luxurious Moisture-Rich Lipstick in Tulip',
 'Kylie Cosmetics Matte Liquid Lipstick & Lip Liner in Posie K',
 'Butter London Plush Rush Lipstick in Playful',
 'Charlotte Tilbury Matte Revolution Lipstick in Pillow Talk',
 'Bite Beauty Amuse Bouche Liquified Lipstick in Chutney',
 'Giorgio Armani Rouge d’Armani Lip Color in Bamboo',
 'CoverGirl Melting Pout Gel Liquid Lipstick in Gelfriend',
 'Nars Powermatte Lip Pigment in Rock With You',
 'Maybelline New York Color Sensational lipstick in Midnight Blue',
 'Clinique Pop Matte Lip Colour + Primer in Shock Pop',
 'Milani Amore Matte Metallic Lip Crème in The Ultimatte',
 'Clarins Joli Rouge Brillant Lipstick in Soft Berry',
 'Rimmel London Oh My Gloss Oil Tint',
 'Maybelline New York Baby Lips Color Balm Crayon',
 'Chantecaille Brilliant Lip Gloss',
 'Chanel Rouge Allure Ink Matte Liquid Lip Colour',
 'Tatcha Camellia Gold Spun Lip Balm',
 'Jack Black Intense Therapy Lip Balm SPF 25',
 'Crest 3D White No Slip Whitestrips With Light',
 'L’Oréal Paris Colour Riche Eye Shadow in Noir C’Est Noir',
 'Revlon ColorStay Crème Eye Shadow in Crème Brûlée',
 'ColourPop Pressed Shadow in Cloud Nine',
 'Mary Kay Mineral Eye Color in Granite',
 'L’Oréal Paris Infallible Paints Metallics Eye Shadow in Brass Knuckles',
 'Givenchy Ombre Couture Cream Eyeshadow in Prune Taffetas',
 'Urban Decay Naked Ultimate Basics',
 'Wander Beauty Unlashed Volume & Curl Mascara',
 'Avon True Color SuperExtend Nourishing Mascara',
 'Maybelline New York The Colossal Big Shot Mascara',
 'Lancôme Monsieur Big Mascara',
 'Em Cosmetics Matte Gel Pencil',
 'Jouer Slim Crème Eyeliner in Matte Brown',
 'L’Oréal Paris Infallible Paints Liquid Eyeliner in Electric Blue',
 'Maybelline New York Curvitude Liner',
 'Shiseido Inkstroke Eyeliner',
 'Bobbi Brown Long-Wear Waterproof Liner',
 'Make Up For Ever Brow Gel',
 'Benefit Gimme Brow',
 'Anastasia Beverly Hills Brow Wiz',
 'CoverGirl Easy Breezy Brow Fill + Shape + Define Powder',
 'RevitaBrow Advanced Eyebrow Conditioner',
 'Garnier SkinActive Micellar Cleansing Water All-in-1',
 'L’Oréal Paris Voluminous Lash Paradise Mascara',
 'Almay Pen Eyeliner',
 'Wet n Wild MegaLast Liquid Catsuit Matte Lipstick',
 'Nyx Away We Glow Liquid Highlighter',
 'Rimmel London Match Perfection Silky Loose Face Powder',
 'CoverGirl Outlast All-Day Soft Touch Concealer',
 'Maybelline New York Brow Precise Fiber Volumizer',
 'Herbal Essences Arabica Coffee Fruit Shampoo',
 'Head & Shoulders Smooth and Silky Shampoo',
 'Pantene Pro-V Daily Moisture Renewal Foam Conditioner',
 'Tresemmé Repair & Protect 7 Instant Recovery Mask',
 'L’Oréal Paris Air Dry It Wave Swept Spray',
 'Suave Avocado + Olive Oil Smoothing Leave-In Conditioning Cream',
 'Dark & Lovely Au Naturale Anti-Shrinkage Clumping Curl Crème Gel',
 'Clean & Clear Acne Triple Clear Bubble Foam Cleanser',
 'Aveeno Positively Radiant In-Shower Facial',
 'Bioré Baking Soda Acne Scrub',
 'St. Ives Exfoliate & Nourish Apricot Oil Scrub',
 'Simple Skincare Hydrating Booster',
 'Nügg Soothing',
 'Neutrogena Makeup Remover Cleansing Towelettes',
 'John Masters Organics Lip Calm',
 'Olay Duo',
 'Vaseline Intensive Care Mature Skin Rejuvenation Healing Moisture Lotion',
 'Nivea Creme Soft Silk Mousse',
 'EOS Shave Cream',
 'Dial Hibiscus Water Body Wash',
 'Dove Shower Foam Deep Moisture Foaming Body Wash',
 'Dyson Supersonic Hair Dryer',
 'Burberry Fresh Glow Highlighter',
 'La Prairie Skin Caviar Absolute Filler',
 'Dior Hydra Life Glow Better Fresh Jelly Mask',
 'Clé de Peau Beauté UV Protective Lip Treatment',
 'Giorgio Armani Power Fabric Longwear High Cover Foundation',
 'Surratt Beauty Artistique Face Brush',
 'Sisley Black Rose Cream Mask',
 'Restorsea Pro Firming Eye Serum',
 'La Mer The Moisturizing Soft Lotion',
 'Elizabeth Arden Prevage City Smart SPF 50 Hydrating Shield',
 'Olay Ultra Moisture Body Wash',
 'Caress Evenly Gorgeous Exfoliating Body Wash',
 'Murad Acne Body Wash',
 'Kopari Coconut Crush Scrub',
 'SheaMoisture 100% Tamanu Oil & Organic Shea Butter Dry Skin Body Lotion',
 'Le Petit Marseillais Shea Butter',
 'L’Occitane Almond Supple Skin Oil',
 'Neutrogena Sheer Zinc Dry-Touch Sunscreen Broad Spectrum SPF 50',
 'St. Tropez Self Tan Express Bronzing Mist',
 'Jergens Natural Glow Daily Moisturizer',
 'Vita Liberata Body Blur Instant HD Skin Finish',
 'Neutrogena Rainbath Restoring Shower and Bath Gel in Fresh Plum',
 'Jason Dry Spray Deodorant',
 'Dove Invisible Dry Spray',
 'Gillette Venus Swirl Razor',
 'Gillette Venus With a Touch of Olay Shave Gel',
 'Yves Saint Laurent Mon Paris',
 ' Gucci Bloom',
 'Diptyque Eau des Sens',
 'Jo Malone London Jade Leaf Tea Cologne',
 'Atelier Cologne Café Tuberosa',
 'Viktor & Rolf Magic Sage Spell',
 'Tom Ford Oud Minérale',
 'Maison Francis Kurkdjian Aqua Universalis Scented Hair Mist',
 "Prada L'Homme Prada Intense",
 'D.S & Durga Tomb of the Eagles Candle',
 'Marc Jacobs Daisy',
 'Calvin Klein Obsessed for Women',
 'Kat Von D Lock-It Edge Foundation Brush',
 'Kevyn Aucoin Duet Concealer Brush',
 'Sephora Collection Pro Airbrush Concealer 57',
 'Smith Cosmetics 202 Microliner Brush',
 'Real Techniques Point XL brush',
 'It Cosmetics Heavenly Luxe French Boutique Blush Brush #4',
 'Revlon Contour Brush',
 'NYX Cosmetics Pro Contour Brush',
 'Lancôme Dual-Ended Fan Brush 31',
 'E.L.F. Beautifully Precise Eyeshadow Brush No. 201',
 ' Smith Cosmetics 202',
 'Anastasia Beverly Hills Duo Brush #12',
 'Sephora Collection Pro Lip Brush 85',
 'Beautyblender Original Makeup Sponge',
 'Beautyblender Micro Minis',
 'Tweezerman Slant Tweezer',
 'BaBylissPro Rapido',
 'GHD White Platinum Styler',
 'T3 Whirl Trio Interchangeable Styling Wand',
 'Tangle Teezer Blow-Styling Round Tool',
 'Christophe Robin Hairbrush',
 'Wet Brush Shower Flex',
 'Neutrogena Light Therapy Acne Mask',
 'Beauty Bioscience GloPro',
 'Tweezerman ProCurl Lash Curler',
 'Kiss Lash Couture Faux Mink Collection in Little Black Dress',
 'Tarte Tarteist Pro Lash Adhesive',
 'Chanel Gitane is Red Polish Perfection',
 'Essie nail polish in Fifth Avenue',
 'Sally Hansen Complete Salon Manicure in Pink a Card',
 'Smith & Cult nail polish in Ghost Edit',
 'OPI Infinite Shine 2 Long-Wear Lacquer in Coconuts Over OPI',
 'Jinsoon nail polish in Beau',
 'Sally Hansen Color Therapy nail polish in Cool Cucumber',
 'Marc Jacobs Beauty Enamored Hi-Shine Nail Polish in Petra',
 'Sally Hansen Miracle Gel',
 'Zoya Naked Manicure Nail Base',
 'Essie Gel Setter Top Coat',
 'Deborah Lippmann The Cure',
 'Cutex Swipe & Go Nail Polish Remover Pads',
 'Supergoop Forever Young Hand Cream SPF 40',
 'The Body Shop Almond Milk and Honey Hand Cream']

In [28]:
# lowering those cases! alhtough i could use my function..

allure_2017 = [i.lower() for i in allure_2017]

In [30]:
len(allure_2017)

237

In [31]:
dict_allure_2017 = {}

for i in range(0,237):
    new_gen = api.search_comments(q = allure_2017[i], 
                                  subreddit = 'SkincareAddiction', 
                                  sort = 'asc', 
                                  fields = ['created_utc', 'score'], 
                                  size = 10)
    dict_allure_2017[allure_2017[i]] = list(new_gen)
    print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236


In [32]:
# this is to get the utc time and score from the reddit posts if there were any 

utc_allure_2017_list = []
score_allure_2017_list = []

for i in list(dict_allure_2017.keys()):
    if dict_allure_2017[i] == []:
        utc_allure_2017_list.append('N/A')
        score_allure_2017_list.append('N/A')
    else:
        d = get_date(dict_allure_2017[i][0].created_utc)
        s = dict_allure_2017[i][0].score
        utc_allure_2017_list.append(d)
        score_allure_2017_list.append(s)

In [ ]:
# here I will pull all the times the subreddit SkincareAddiction has mentioned the products/brands
# on the Sephora 2018 best item's list

# best_text_list = [best_brand_name, best_product_name]
# data_dict_best = {}

# for j in best_text_list:
#     for i in range(0,200):
#         new_gen = api.search_comments(q = j[i], 
#                                   subreddit = 'SkincareAddiction', 
#                                   sort = 'asc', 
#                                   fields = ['created_utc', 'score'], 
#                                   size = 10)
#         data_dict_best[j[i]] = list(new_gen)
#         print(i)

In [ ]:
# here I will get the time stamps and scores of the posts in the new product category

# utc_new_list = []
# score_new_list = []

# for i in list(data_dict_new.keys()):
#     if data_dict_new[i] == []:
#         utc_new_list.append('N/A')
#         score_new_list.append('N/A')
#     else:
#         d = get_date(data_dict_new[i][0].created_utc)
#         s = data_dict_new[i][0].score
#         utc_new_list.append(d)
#         score_new_list.append(s)

In [ ]:
# here I will get the time stamps and scores of the posts in the best product category

# utc_best_list = []
# score_best_list = []

# for i in list(data_dict_best.keys()):
#     if data_dict_best[i] == []:
#         utc_best_list.append('N/A')
#         score_best_list.append('N/A')
#     else:
#         d = get_date(data_dict_best[i][0].created_utc)
#         s = data_dict_best[i][0].score
#         utc_best_list.append(d)
#         score_best_list.append(s)

In [33]:
# setting the product names

#product_new = list(data_dict_new.keys())
#product_best = list(data_dict_best.keys())
product_allure_2017 = list(dict_allure_2017.keys())
product_combo = list(data_new.keys())
#product_source = 

In [129]:
# importing my into the gloss dataset 

itg_df = pd.DataFrame.from_csv('./CSVs/ITG_final.csv')

/Users/emmaeleanoryork/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: from_csv is deprecated. Please use read_csv(...) instead. Note that some of the default arguments are different, so please refer to the documentation for from_csv when changing your function calls
  """Entry point for launching an IPython kernel.


In [130]:
itg_df.head()

ITG Products        Date
0  Lord Jones All Natural Old Fashioned High CBD ...  1517360461
1                         Augustinus Bader The Cream  1517360461
2                  L'Oréal Voluminous Feline Mascara  1517360461
3              Ole Henriksen Banana Bright Eye Crème  1517360461
4              YSL Tatouage Couture Matte Stain in 7  1517360461

In [133]:
itg_df.rename(index=str, 
              columns={"ITG Products": "Products", "Date": "ITG Posting Date"}, 
              inplace = True)

In [134]:
itg_df.head()

Products  ITG Posting Date
0  Lord Jones All Natural Old Fashioned High CBD ...        1517360461
1                         Augustinus Bader The Cream        1517360461
2                  L'Oréal Voluminous Feline Mascara        1517360461
3              Ole Henriksen Banana Bright Eye Crème        1517360461
4              YSL Tatouage Couture Matte Stain in 7        1517360461

In [135]:
itg_df['ITG Posting Date'] = pd.to_datetime(itg_df['ITG Posting Date'], unit = "s")

In [137]:
itg_df['Products'] = itg_df['Products'].str.lower()

In [161]:
itg_df['ITG Posting Date']

0    2018-01-31 01:01:01
1    2018-01-31 01:01:01
2    2018-01-31 01:01:01
3    2018-01-31 01:01:01
4    2018-01-31 01:01:01
5    2018-01-31 01:01:01
6    2018-01-31 01:01:01
7    2018-01-31 01:01:01
8    2018-02-28 01:01:01
9    2018-02-28 01:01:01
10   2018-02-28 01:01:01
11   2018-02-28 01:01:01
12   2018-02-28 01:01:01
13   2018-02-28 01:01:01
14   2018-02-28 01:01:01
15   2018-02-28 01:01:01
16   2018-03-31 01:01:01
17   2018-03-31 01:01:01
18   2018-03-31 01:01:01
19   2018-03-31 01:01:01
20   2018-03-31 01:01:01
21   2018-03-31 01:01:01
22   2018-03-31 01:01:01
23   2018-04-30 01:01:01
24   2018-04-30 01:01:01
25   2018-04-30 01:01:01
26   2018-04-30 01:01:01
27   2018-04-30 01:01:01
28   2018-04-30 01:01:01
29   2018-04-30 01:01:01
             ...        
48   2018-07-31 01:01:01
49   2018-07-31 01:01:01
50   2018-07-31 01:01:01
51   2018-07-31 01:01:01
52   2018-07-31 01:01:01
53   2018-07-31 01:01:01
54   2018-07-31 01:01:01
55   2018-07-31 01:01:01
56   2018-07-31 01:01:01


In [139]:
itg_df['Source'] = 'ITG'

In [177]:
itg = itg_df['Products'].tolist()
itg_date = itg_df['ITG Posting Date'].tolist()

In [142]:
len(itg)

78

In [146]:
dict_itg = {}

for i in range(0,78):
    new_gen = api.search_comments(q = itg[i], 
                                  subreddit = 'SkincareAddiction', 
                                  sort = 'asc', 
                                  fields = ['created_utc', 'score'], 
                                  size = 10)
    dict_itg[itg[i]] = list(new_gen)
    print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77


In [149]:
utc_itg_list = []
score_itg_list = []

for i in list(dict_itg.keys()):
    if dict_itg[i] == []:
        utc_itg_list.append('N/A')
        score_itg_list.append('N/A')
    else:
        d = get_date(dict_itg[i][0].created_utc)
        s = dict_itg[i][0].score
        utc_itg_list.append(d)
        score_itg_list.append(s)

In [168]:
# making those dataframes!

df_allure_2017 = pd.DataFrame()
df_sephora_combo = pd.DataFrame()
df_itg = pd.DataFrame()

df = pd.DataFrame()

In [169]:
product_allure_2017 = list(dict_allure_2017.keys())
product_combo = list(data_new.keys())
product_itg = list(dict_itg.keys())

In [178]:
# df_sephora_new['Product Name'] = product_new
# df_sephora_new['Posting Date'] = utc_new_list
# df_sephora_new['Upvotes'] = score_new_list
# df_sephora_new['Source'] = 'Sephora New'
# #df_sephora_new['Date on Sephora'] = 1539738061

# df_sephora_best['Product Name'] = product_best
# df_sephora_best['Posting Date'] = utc_best_list
# df_sephora_best['Upvotes'] = score_best_list
# df_sephora_best['Source'] = 'Sephora Best'

df_allure_2017['Product Name'] = product_allure_2017
df_allure_2017['Reddit Posting Date'] = utc_allure_2017_list
df_allure_2017['Upvotes'] = score_allure_2017_list
df_allure_2017['Source'] = 'Allure Best of Beauty 2017'

df_sephora_combo['Product Name'] = product_combo
df_sephora_combo['Reddit Posting Date'] = utc_combo_list
df_sephora_combo['Upvotes'] = score_combo_list
df_sephora_combo['Source'] = 'Sephora New Combo'

df_itg['Product Name'] = product_itg
df_itg['Reddit Posting Date'] = utc_itg_list
df_itg['Upvotes'] = score_itg_list
df_itg['Source'] = 'ITG'
df_itg['ITG Posting Date'] = itg_date

In [179]:
#df_sephora_new.to_csv('./sephora_new_ska.csv')
#df_sephora_best.to_csv('./sephora_best_ska.csv')
df_allure_2017.to_csv('./allure_2017_ska.csv')
df_sephora_combo.to_csv('./sephora_combo_ska.csv')
df_itg.to_csv('./df_itg.to_csv')

In [180]:
df_total = pd.DataFrame()

In [181]:
df_total = df_sephora_combo.append([df_allure_2017, df_itg], ignore_index = True)

/Users/emmaeleanoryork/anaconda3/lib/python3.6/site-packages/pandas/core/frame.py:6211: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  sort=sort)


In [182]:
df_total.head()

ITG Posting Date                                       Product Name  \
0              NaT                  dr. jart+ mask heroes face savers   
1              NaT  moon juice beauty shroom vegan collagen protec...   
2              NaT   moon juice beauty shroom exfoliating acid potion   
3              NaT                 sephora collection face mask magic   
4              NaT                       laneige kiss and make up set   

   Reddit Posting Date             Source Upvotes  
0                  N/A  Sephora New Combo     N/A  
1                  N/A  Sephora New Combo     N/A  
2                  N/A  Sephora New Combo     N/A  
3                  N/A  Sephora New Combo     N/A  
4  2018-09-30 01:50:52  Sephora New Combo       1

In [183]:
df_total.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 655 entries, 0 to 654
Data columns (total 5 columns):
ITG Posting Date       78 non-null datetime64[ns]
Product Name           655 non-null object
Reddit Posting Date    655 non-null object
Source                 655 non-null object
Upvotes                655 non-null object
dtypes: datetime64[ns](1), object(4)
memory usage: 25.7+ KB


## now I want to see what the time difference is between when the products were posted on Sephora's website vs when reddit or Allure talked about them

In [184]:
df_total['On Reddit'] = (df_total['Reddit Posting Date'] != 'N/A').astype(int)
df_total['On Sephora'] = (df_total['Source'].str.contains('Sephora')).astype(int)
df_total['On Allure'] = (df_total['Source'].str.contains('Allure')).astype(int)
df_total['On ITG'] = (df_total['Source'].str.contains('ITG')).astype(int)

In [215]:
df_total['Allure Posting Date'] = np.where(df_total['On Allure'] == True, get_date(1505696461), None)
#df_total['Sephora Posting']

In [217]:
df_total['Sephora Post Date'] = np.where(df_total['On Sephora'] == True, get_date(1539824461), None)

In [220]:
df_total.head()

ITG Posting Date                                       Product Name  \
0              NaT                  dr. jart+ mask heroes face savers   
1              NaT  moon juice beauty shroom vegan collagen protec...   
2              NaT   moon juice beauty shroom exfoliating acid potion   
3              NaT                 sephora collection face mask magic   
4              NaT                       laneige kiss and make up set   

   Reddit Posting Date             Source Upvotes  On Reddit  On Sephora  \
0                  N/A  Sephora New Combo     N/A          0           1   
1                  N/A  Sephora New Combo     N/A          0           1   
2                  N/A  Sephora New Combo     N/A          0           1   
3                  N/A  Sephora New Combo     N/A          0           1   
4  2018-09-30 01:50:52  Sephora New Combo       1          1           1   

   On Allure  On ITG Allure Posting Date Time from 1st Reddit Post  \
0          0       0                 NaT                       N/A   
1          0       0                 NaT                       N/A   
2          0       0                 NaT                       N/A   
3          0       0                 NaT                       N/A   
4          0       0                 NaT  -19 days, 5:13:18.247947   

    Sephora Post Date  
0 2018-10-17 21:01:01  
1 2018-10-17 21:01:01  
2 2018-10-17 21:01:01  
3 2018-10-17 21:01:01  
4 2018-10-17 21:01:01

In [198]:
df_total.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 655 entries, 0 to 654
Data columns (total 10 columns):
ITG Posting Date       78 non-null datetime64[ns]
Product Name           655 non-null object
Reddit Posting Date    655 non-null object
Source                 655 non-null object
Upvotes                655 non-null object
On Reddit              655 non-null int64
On Sephora             655 non-null int64
On Allure              655 non-null int64
On ITG                 655 non-null int64
Allure Posting Date    655 non-null object
dtypes: datetime64[ns](1), int64(4), object(5)
memory usage: 51.2+ KB


In [226]:
get_date(1539824461)

datetime.datetime(2018, 10, 17, 21, 1, 1)

In [229]:
df_total.loc[4, 'Reddit Posting Date'] - get_date(1539824461)

datetime.timedelta(-18, 17391)

In [231]:
sephora_date = get_date(1539824461)

In [255]:
# find time difference from first original post to Sephora 

diff_time = []

for i in range(len(df_total['Reddit Posting Date'])):
    if df_total.loc[i, 'Reddit Posting Date'] == 'N/A':
        diff_time.append('N/A')
    else:
        diff_time.append((df_total.loc[i,'Reddit Posting Date']) - sephora_date)

In [257]:
#dt.datetime.now()

In [258]:
diff_time_a = []

for i in range(len(df_total['Allure Posting Date'])):
    if df_total.loc[i, 'Allure Posting Date'] == None:
        diff_time_a.append('N/A')
    else:
        diff_time_a.append((df_total.loc[i,'Allure Posting Date']) - sephora_date)

In [259]:
len(diff_time_a)

655

In [260]:
df_total['Time from 1st Reddit Post'] = diff_time
df_total['Time from 1st Allure Post'] = diff_time_a

In [261]:
df_total.head()

ITG Posting Date                                       Product Name  \
0              NaT                  dr. jart+ mask heroes face savers   
1              NaT  moon juice beauty shroom vegan collagen protec...   
2              NaT   moon juice beauty shroom exfoliating acid potion   
3              NaT                 sephora collection face mask magic   
4              NaT                       laneige kiss and make up set   

   Reddit Posting Date             Source Upvotes  On Reddit  On Sephora  \
0                  N/A  Sephora New Combo     N/A          0           1   
1                  N/A  Sephora New Combo     N/A          0           1   
2                  N/A  Sephora New Combo     N/A          0           1   
3                  N/A  Sephora New Combo     N/A          0           1   
4  2018-09-30 01:50:52  Sephora New Combo       1          1           1   

   On Allure  On ITG Allure Posting Date Time from 1st Reddit Post  \
0          0       0                 NaT                       N/A   
1          0       0                 NaT                       N/A   
2          0       0                 NaT                       N/A   
3          0       0                 NaT                       N/A   
4          0       0                 NaT         -18 days, 4:49:51   

    Sephora Post Date    Time Difference Time from 1st Allure Post  
0 2018-10-17 21:01:01                N/A                       NaT  
1 2018-10-17 21:01:01                N/A                       NaT  
2 2018-10-17 21:01:01                N/A                       NaT  
3 2018-10-17 21:01:01                N/A                       NaT  
4 2018-10-17 21:01:01  -18 days, 4:49:51                       NaT

In [10]:
df_total['On Sephora'].value_counts()

NameError: name 'df_total' is not defined

In [254]:
df_total['Allure Posting Date'].value_counts()

2017-09-17 21:01:01    237
Name: Allure Posting Date, dtype: int64

In [262]:
df_total.to_csv('./CSVs/df_total.csv')

In [13]:
df_total = pd.read_csv('./CSVs/df_total.csv')

In [14]:
df_total.head()

Unnamed: 0 ITG Posting Date  \
0           0              NaN   
1           1              NaN   
2           2              NaN   
3           3              NaN   
4           4              NaN   

                                        Product Name  Reddit Posting Date  \
0                  dr. jart+ mask heroes face savers                  NaN   
1  moon juice beauty shroom vegan collagen protec...                  NaN   
2   moon juice beauty shroom exfoliating acid potion                  NaN   
3                 sephora collection face mask magic                  NaN   
4                       laneige kiss and make up set  2018-09-30 01:50:52   

              Source  Upvotes  On Reddit  On Sephora  On Allure  On ITG  \
0  Sephora New Combo      NaN          0           1          0       0   
1  Sephora New Combo      NaN          0           1          0       0   
2  Sephora New Combo      NaN          0           1          0       0   
3  Sephora New Combo      NaN          0           1          0       0   
4  Sephora New Combo      1.0          1           1          0       0   

  Allure Posting Date Time from 1st Reddit Post    Sephora Post Date  \
0                 NaN                       NaN  2018-10-17 21:01:01   
1                 NaN                       NaN  2018-10-17 21:01:01   
2                 NaN                       NaN  2018-10-17 21:01:01   
3                 NaN                       NaN  2018-10-17 21:01:01   
4                 NaN         -18 days, 4:49:51  2018-10-17 21:01:01   

     Time Difference Time from 1st Allure Post  
0                NaN                       NaN  
1                NaN                       NaN  
2                NaN                       NaN  
3                NaN                       NaN  
4  -18 days, 4:49:51                       NaN

In [18]:
df_total['On Sephora'].value_counts()

1    340
0    315
Name: On Sephora, dtype: int64

### Here I will check all of the product types through all of the subreddits and see how often the terms show up

In [22]:
products_to_test = df_total['Product Name'].tolist()

In [23]:
type(products_to_test)

list

In [25]:
len(products_to_test)

655

In [30]:
products_to_test[3]

'sephora collection face mask magic'

In [34]:
p_dict = {}

for i in range(0,655):
    new_gen = api.search_comments(q = products_to_test[i],
                                 aggs = 'subreddit',
                                 fields = ['doc_count', 'key', 'created_utc'],
                                 sort = 'asc',
                                 sort_type = 'created_utc',
                                 size = 0)
    p_dict[products_to_test[i]] = list(new_gen)
    print(i)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [35]:
p_dict

{'dr. jart+ mask heroes face savers': [{'subreddit': []}],
 'moon juice beauty shroom vegan collagen protection': [{'subreddit': []}],
 'moon juice beauty shroom exfoliating acid potion': [{'subreddit': [{'doc_count': 1,
     'key': 'scacjdiscussion'}]},
  comment(created_utc=1538687138, created=1538701538.0, d_={'created_utc': 1538687138, 'created': 1538701538.0})],
 'sephora collection face mask magic': [{'subreddit': [{'doc_count': 3,
     'key': 'MakeupAddiction'},
    {'doc_count': 2, 'key': 'BeautyAddiction'},
    {'doc_count': 1, 'key': 'AsianBeauty'},
    {'doc_count': 1, 'key': 'AustralianMakeup'},
    {'doc_count': 1, 'key': 'FeminineNotFeminist'},
    {'doc_count': 1, 'key': 'MakeupRehab'}]},
  comment(created_utc=1416760881, created=1416775281.0, d_={'created_utc': 1416760881, 'created': 1416775281.0}),
  comment(created_utc=1435796398, created=1435810798.0, d_={'created_utc': 1435796398, 'created': 1435810798.0}),
  comment(created_utc=1438544775, created=1438559175.0, d_=

In [140]:
p_dict['laneige kiss and make up set']

[{'subreddit': [{'doc_count': 4, 'key': 'AsianBeauty'},
   {'doc_count': 1, 'key': 'AsianBeautyAdvice'},
   {'doc_count': 1, 'key': 'SkincareAddiction'},
   {'doc_count': 1, 'key': 'abdiscussion'}]},
 comment(created_utc=1398794628, created=1398809028.0, d_={'created_utc': 1398794628, 'created': 1398809028.0}),
 comment(created_utc=1433386114, created=1433400514.0, d_={'created_utc': 1433386114, 'created': 1433400514.0}),
 comment(created_utc=1442938594, created=1442952994.0, d_={'created_utc': 1442938594, 'created': 1442952994.0}),
 comment(created_utc=1491188460, created=1491202860.0, d_={'created_utc': 1491188460, 'created': 1491202860.0}),
 comment(created_utc=1502442884, created=1502457284.0, d_={'created_utc': 1502442884, 'created': 1502457284.0}),
 comment(created_utc=1510576438, created=1510590838.0, d_={'created_utc': 1510576438, 'created': 1510590838.0}),
 comment(created_utc=1538286652, created=1538301052.0, d_={'created_utc': 1538286652, 'created': 1538301052.0})]

In [45]:
p_dict['sephora collection face mask magic']

[{'subreddit': [{'doc_count': 3, 'key': 'MakeupAddiction'},
   {'doc_count': 2, 'key': 'BeautyAddiction'},
   {'doc_count': 1, 'key': 'AsianBeauty'},
   {'doc_count': 1, 'key': 'AustralianMakeup'},
   {'doc_count': 1, 'key': 'FeminineNotFeminist'},
   {'doc_count': 1, 'key': 'MakeupRehab'}]},
 comment(created_utc=1416760881, created=1416775281.0, d_={'created_utc': 1416760881, 'created': 1416775281.0}),
 comment(created_utc=1435796398, created=1435810798.0, d_={'created_utc': 1435796398, 'created': 1435810798.0}),
 comment(created_utc=1438544775, created=1438559175.0, d_={'created_utc': 1438544775, 'created': 1438559175.0}),
 comment(created_utc=1445183371, created=1445197771.0, d_={'created_utc': 1445183371, 'created': 1445197771.0}),
 comment(created_utc=1478311771, created=1478326171.0, d_={'created_utc': 1478311771, 'created': 1478326171.0}),
 comment(created_utc=1500574726, created=1500589126.0, d_={'created_utc': 1500574726, 'created': 1500589126.0}),
 comment(created_utc=1512102

In [67]:
p_dict['sephora collection face mask magic'][0]['subreddit'][0]

{'doc_count': 3, 'key': 'MakeupAddiction'}

In [79]:
p_dict['sephora collection face mask magic'][0]['subreddit'][0]['doc_count']

3

In [77]:
p_dict['sephora collection face mask magic'][1].created_utc

1416760881

In [125]:
p_dict['dr. jart+ mask heroes face savers'][0]['subreddit']

[]

In [90]:
p_dict['sephora collection face mask magic'][0]['subreddit']

[{'doc_count': 3, 'key': 'MakeupAddiction'},
 {'doc_count': 2, 'key': 'BeautyAddiction'},
 {'doc_count': 1, 'key': 'AsianBeauty'},
 {'doc_count': 1, 'key': 'AustralianMakeup'},
 {'doc_count': 1, 'key': 'FeminineNotFeminist'},
 {'doc_count': 1, 'key': 'MakeupRehab'}]

In [143]:
p_dict['sephora collection face mask magic'][0]['subreddit'][0]['doc_count']

3

In [88]:
for i in range(len(p_dict['sephora collection face mask magic'][0]['subreddit'])):
    print(i)

0
1
2
3
4
5


In [150]:
[int(j) for j in range(len(p_dict['sephora collection face mask magic'][0]['subreddit']))]

[0, 1, 2, 3, 4, 5]

In [163]:
p_dict['sephora collection face mask magic'][0]['subreddit'][2]['doc_count']

1

# !!!THIS IS MY ACTUAL CODE TO CHECK WHICH SUBREDDITS THE PRODUCTS ARE ON!!!

In [313]:
p_first_comment_date = []
p_name = []
p_doc_count = []
p_key = []


for i in list(p_dict.keys()):
    if p_dict[i][0]['subreddit'] == []:
        p_first_comment_date.append('N/A')
        p_doc_count.append(0)
        p_key.append('N/A')
        p_name.append(i)
    else:
        d = get_date(p_dict[i][1].created_utc)
        n = [p_dict[i][0]['subreddit'][j]['doc_count'] for j in range(len(p_dict[i][0]['subreddit']))]
        key = [p_dict[i][0]['subreddit'][j]['key'] for j in range(len(p_dict[i][0]['subreddit']))]
        p_first_comment_date.append(d)
        p_doc_count.append(n)
        p_key.append(key)
        p_name.append(i)

In [170]:
len(p_name), len(p_key)

(654, 654)

In [438]:
p_first_comment_date

['N/A',
 'N/A',
 datetime.datetime(2018, 10, 4, 17, 5, 38),
 datetime.datetime(2014, 11, 23, 11, 41, 21),
 datetime.datetime(2014, 4, 29, 14, 3, 48),
 datetime.datetime(2018, 10, 6, 12, 16, 55),
 datetime.datetime(2018, 8, 24, 19, 33, 24),
 datetime.datetime(2017, 2, 15, 6, 18, 1),
 datetime.datetime(2018, 10, 17, 7, 24, 33),
 'N/A',
 'N/A',
 datetime.datetime(2017, 9, 9, 12, 53, 14),
 datetime.datetime(2014, 8, 6, 11, 4, 2),
 'N/A',
 datetime.datetime(2018, 8, 30, 10, 43, 27),
 'N/A',
 datetime.datetime(2018, 3, 4, 21, 26, 56),
 datetime.datetime(2018, 9, 16, 13, 50, 41),
 'N/A',
 datetime.datetime(2018, 10, 12, 22, 31, 13),
 datetime.datetime(2018, 7, 31, 16, 49, 59),
 'N/A',
 datetime.datetime(2018, 9, 30, 5, 11, 4),
 'N/A',
 'N/A',
 'N/A',
 datetime.datetime(2017, 10, 13, 8, 29, 4),
 datetime.datetime(2011, 9, 21, 14, 16, 38),
 datetime.datetime(2018, 10, 10, 15, 14, 25),
 datetime.datetime(2017, 4, 4, 18, 42, 8),
 datetime.datetime(2018, 10, 8, 1, 16, 11),
 datetime.datetime(2016,

In [458]:
p_name

['dr. jart+ mask heroes face savers',
 'moon juice beauty shroom vegan collagen protection',
 'moon juice beauty shroom exfoliating acid potion',
 'sephora collection face mask magic',
 'laneige kiss and make up set',
 'drunk elephant agent ellie day kit',
 'olehenriksen glow cycle retin-alt power serum',
 'welleco the super elixir',
 'la mer merry little miracles',
 'drunk elephant inspector drunk night kit',
 'sol de janeiro bum bum carnaval extravaganza',
 'tatcha skincare for makeup lovers obento box',
 'fresh sugar jetsetter',
 'olehenriksen glow brightly - radiance-boosting super set',
 'farmacy honeymoon glow aha resurfacing night serum with echinacea greenenvy',
 'drunk elephant the big reveal kit',
 'herbivore jade facial roller',
 'summer fridays overtime mask',
 'fresh sky high-dration',
 'sunday riley good genes holiday kit',
 'fresh destination sugar',
 'algenist secrets of algae kit',
 'peter thomas roth mask frenzy',
 'olehenriksen goodnight glow retin-alt sleeping crème

In [443]:
dates = list(filter(lambda a: a != 'N/A', p_first_comment_date))

In [274]:
p_key

['N/A',
 'N/A',
 ['scacjdiscussion'],
 ['MakeupAddiction',
  'BeautyAddiction',
  'AsianBeauty',
  'AustralianMakeup',
  'FeminineNotFeminist',
  'MakeupRehab'],
 ['AsianBeauty', 'AsianBeautyAdvice', 'SkincareAddiction', 'abdiscussion'],
 ['MUAontheCheap'],
 ['muacjdiscussion'],
 ['SkincareAddiction',
  'BeautyBoxes',
  'TheColorIsRed',
  'eczema',
  'veganfitness'],
 ['MUAontheCheap'],
 'N/A',
 'N/A',
 ['AsianBeautyRehab', 'MakeupAddiction', 'MakeupAddictionCanada'],
 ['cocktails', 'makeupflatlays', 'muacjdiscussion'],
 'N/A',
 ['MUAontheCheap'],
 'N/A',
 ['SkincareAddiction'],
 ['SkincareAddiction'],
 'N/A',
 ['MakeupAddictionCanada',
  'AsianBeauty',
  'MakeupAddiction',
  'MUAontheCheap',
  'MakeupRehab',
  'Sephora'],
 ['AskReddit',
  'WritingPrompts',
  'loseit',
  'Scotch',
  'worldbuilding',
  '3DS',
  '90daysgoal',
  'AMA',
  'AdviceAnimals',
  'AirBnB',
  'AskCulinary',
  'AskFoodHistorians',
  'AskHistorians',
  'Australia_',
  'AutoNewspaper',
  'Baking',
  'CasualConversat

In [651]:
p_doc_count[:]

[0,
 0,
 [1],
 [3, 2, 1, 1, 1, 1],
 [4, 1, 1, 1],
 [1],
 [1],
 [2, 1, 1, 1, 1],
 [1],
 0,
 0,
 [1, 1, 1],
 [1, 1, 1],
 0,
 [1],
 0,
 [1],
 [2],
 0,
 [3, 2, 2, 1, 1, 1],
 [12,
  3,
  3,
  2,
  2,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1,
  1],
 0,
 [1, 1],
 0,
 0,
 0,
 [1, 1, 1, 1],
 [1997,
  439,
  431,
  277,
  255,
  204,
  191,
  172,
  164,
  153,
  134,
  121,
  106,
  83,
  77,
  77,
  75,
  74,
  73,
  71,
  65,
  63,
  61,
  61,
  56,
  55,
  51,
  47,
  45,
  44,
  44,
  44,
  42,
  41,
  39,
  39,
  38,
  37,
  35,
  33,
  32,
  31,
  30,
  30,
  30,
  29,
  29,
  28,
  28,
  27,
  26,
  25,
  25,
  24,
  23,
  23,
  23,
  22,
  22,
  22,
  22,
  22,
  22,
  22,
  22,
  21,
  21,
  20,
  20,
  20,
  20,
  19,
  19,
  19,
  19,
  18,
  18,
  18,
  18,
  18,
  18,

In [656]:
df_final = pd.DataFrame()

In [672]:
df_final['Product Name'] = p_name
df_final['Subreddit'] = p_key
df_final['Times Mentioned'] = p_doc_count
df_final['Sephora?'] = (df_total['Source'].str.contains('Sephora')).astype(int)

In [661]:
df_final.head()

Product Name  \
0                  dr. jart+ mask heroes face savers   
1  moon juice beauty shroom vegan collagen protec...   
2   moon juice beauty shroom exfoliating acid potion   
3                 sephora collection face mask magic   
4                       laneige kiss and make up set   

                                           Subreddit     Times Mentioned  \
0                                                N/A                   0   
1                                                N/A                   0   
2                                  [scacjdiscussion]                 [1]   
3  [MakeupAddiction, BeautyAddiction, AsianBeauty...  [3, 2, 1, 1, 1, 1]   
4  [AsianBeauty, AsianBeautyAdvice, SkincareAddic...        [4, 1, 1, 1]   

   Sephora?  
0         1  
1         1  
2         1  
3         1  
4         1

In [673]:
print(df_final.dtypes)

Product Name       object
Subreddit          object
Times Mentioned    object
Sephora?            int64
dtype: object


In [674]:
df_final[['Sephora?', 'Times Mentioned']] = df_final[['Sephora?', 'Times Mentioned']].astype(object)

In [675]:
print(df_final.dtypes)

Product Name       object
Subreddit          object
Times Mentioned    object
Sephora?           object
dtype: object


In [592]:
df_final.iterrows()

<generator object DataFrame.iterrows at 0x1a9eef4048>

In [585]:
import sys
print (sys.version)

3.6.5 |Anaconda, Inc.| (default, Apr 26 2018, 08:42:37) 
[GCC 4.2.1 Compatible Clang 4.0.1 (tags/RELEASE_401/final)]


In [647]:
df1 = pd.concat([df_final['Product Name'], 
                 df_final['Sephora?'],
                 df_final['Subreddit'][:],
                df_final['Times Mentioned'][:]], axis = 1)

In [648]:
df1.head()

Product Name  Sephora?  \
0                  dr. jart+ mask heroes face savers         1   
1  moon juice beauty shroom vegan collagen protec...         1   
2   moon juice beauty shroom exfoliating acid potion         1   
3                 sephora collection face mask magic         1   
3                 sephora collection face mask magic         1   

         Subreddit  Times Mentioned  
0              N/A              0.0  
1              N/A              0.0  
2  scacjdiscussion              1.0  
3  MakeupAddiction              3.0  
3  BeautyAddiction              3.0

In [614]:
df1['Times Mentioned'] = df_final['Times Mentioned'][:]

In [615]:
df1.head()

Product Name  Sephora?  \
0                  dr. jart+ mask heroes face savers         1   
1  moon juice beauty shroom vegan collagen protec...         1   
2   moon juice beauty shroom exfoliating acid potion         1   
3                 sephora collection face mask magic         1   
3                 sephora collection face mask magic         1   

         Subreddit  Times Mentioned  
0              N/A              0.0  
1              N/A              0.0  
2  scacjdiscussion              1.0  
3  MakeupAddiction              3.0  
3  BeautyAddiction              3.0

In [824]:
# exploded_dfs = []
# for _, row in df_final.iterrows():
#     if all(row): # if a row does contain all non-None values
#         # Put 1st pair of columns into single DF, exploding single
#         # cell into multiple rows as needed
#         df1 = pd.concat([pd.Series([row['Product Name'],
#                                    row['Subreddit'][:]])], ignore_index = True)
#         # Assign column names
#         df1.columns = ['Subreddit', 'Product Name']
#         # Put 2nd pair of columns into single DF, exploding single
#         # cell into multiple rows as needed
#         df2 = pd.concat([pd.Series([row['Product Name'], 
#                                    row['Times Mentioned'][:]])], ignore_index = True)
#         # Assign column names
#         df2.columns = ['Times Mentioned', 'Product Name']
#         # Perform INNER JOIN on DFs with exploded row contents
#         # & drop duplicated column
#         merged = pd.concat([df1, df2], axis=1)
#         merged = merged.loc[:,~merged.columns.duplicated()]
#         # Swap 1st and 2nd columns
#         cols = list(merged)
#         cols.insert(0, cols.pop(cols.index('Product Name')))
#         merged = merged.loc[:, cols]
#     else: # if a row does not contain all non-None values
#         # Create single row DF with no changes
#         merged = pd.DataFrame(columns=['Product Name', 'Subreddit',
#                                       'Times Mentioned'])
#         # Append row to DF
#         merged.loc[0] = row
#     exploded_dfs.append(merged)

# # Vertically concatenate DFs in list
# print(pd.concat(exploded_dfs, axis=0).reset_index(drop=True))

In [728]:
l = ['Subreddit', 'Times Mentioned']

In [825]:
test = df_final.set_index(['Product Name', 
                    'Sephora?'])['Subreddit'].apply(pd.Series).stack().reset_index(['Product Name', 
                                                                                    'Sephora?'], 
                                                                                    name = 'Subreddit')

In [826]:
test

Product Name  Sephora?  \
0                   dr. jart+ mask heroes face savers         1   
0   moon juice beauty shroom vegan collagen protec...         1   
0    moon juice beauty shroom exfoliating acid potion         1   
0                  sephora collection face mask magic         1   
1                  sephora collection face mask magic         1   
2                  sephora collection face mask magic         1   
3                  sephora collection face mask magic         1   
4                  sephora collection face mask magic         1   
5                  sephora collection face mask magic         1   
0                        laneige kiss and make up set         1   
1                        laneige kiss and make up set         1   
2                        laneige kiss and make up set         1   
3                        laneige kiss and make up set         1   
0                  drunk elephant agent ellie day kit         1   
0       olehenriksen glow cycle retin-alt power serum         1   
0                            welleco the super elixir         1   
1                            welleco the super elixir         1   
2                            welleco the super elixir         1   
3                            welleco the super elixir         1   
4                            welleco the super elixir         1   
0                        la mer merry little miracles         1   
0            drunk elephant inspector drunk night kit         1   
0        sol de janeiro bum bum carnaval extravaganza         1   
0        tatcha skincare for makeup lovers obento box         1   
1        tatcha skincare for makeup lovers obento box         1   
2        tatcha skincare for makeup lovers obento box         1   
0                               fresh sugar jetsetter         1   
1                               fresh sugar jetsetter         1   
2                               fresh sugar jetsetter         1   
0   olehenriksen glow brightly - radiance-boosting...         1   
..                                                ...       ...   
15     the ordinary natural moisturizing factors + ha         0   
16     the ordinary natural moisturizing factors + ha         0   
17     the ordinary natural moisturizing factors + ha         0   
18     the ordinary natural moisturizing factors + ha         0   
19     the ordinary natural moisturizing factors + ha         0   
20     the ordinary natural moisturizing factors + ha         0   
21     the ordinary natural moisturizing factors + ha         0   
22     the ordinary natural moisturizing factors + ha         0   
23     the ordinary natural moisturizing factors + ha         0   
24     the ordinary natural moisturizing factors + ha         0   
25     the ordinary natural moisturizing factors + ha         0   
26     the ordinary natural moisturizing factors + ha         0   
27     the ordinary natural moisturizing factors + ha         0   
28     the ordinary natural moisturizing factors + ha         0   
29     the ordinary natural moisturizing factors + ha         0   
30     the ordinary natural moisturizing factors + ha         0   
31     the ordinary natural moisturizing factors + ha         0   
32     the ordinary natural moisturizing factors + ha         0   
33     the ordinary natural moisturizing factors + ha         0   
34     the ordinary natural moisturizing factors + ha         0   
35     the ordinary natural moisturizing factors + ha         0   
36     the ordinary natural moisturizing factors + ha         0   
37     the ordinary natural moisturizing factors + ha         0   
38     the ordinary natural moisturizing factors + ha         0   
39     the ordinary natural moisturizing factors + ha         0   
40     the ordinary natural moisturizing factors + ha         0   
41     the ordinary natural moisturizing factors + ha         0   
42     the ordinary natural moisturizing factors + ha         0   
43     the ordinary n

In [827]:
test_2 = df_final.set_index(['Product Name'])['Times Mentioned'].apply(pd.Series).stack().reset_index(['Product Name'],
                                                                                            name = 'Times Mentioned')

In [828]:
test_2

Product Name  Times Mentioned
0                   dr. jart+ mask heroes face savers              0.0
0   moon juice beauty shroom vegan collagen protec...              0.0
0    moon juice beauty shroom exfoliating acid potion              1.0
0                  sephora collection face mask magic              3.0
1                  sephora collection face mask magic              2.0
2                  sephora collection face mask magic              1.0
3                  sephora collection face mask magic              1.0
4                  sephora collection face mask magic              1.0
5                  sephora collection face mask magic              1.0
0                        laneige kiss and make up set              4.0
1                        laneige kiss and make up set              1.0
2                        laneige kiss and make up set              1.0
3                        laneige kiss and make up set              1.0
0                  drunk elephant agent ellie day kit              1.0
0       olehenriksen glow cycle retin-alt power serum              1.0
0                            welleco the super elixir              2.0
1                            welleco the super elixir              1.0
2                            welleco the super elixir              1.0
3                            welleco the super elixir              1.0
4                            welleco the super elixir              1.0
0                        la mer merry little miracles              1.0
0            drunk elephant inspector drunk night kit              0.0
0        sol de janeiro bum bum carnaval extravaganza              0.0
0        tatcha skincare for makeup lovers obento box              1.0
1        tatcha skincare for makeup lovers obento box              1.0
2        tatcha skincare for makeup lovers obento box              1.0
0                               fresh sugar jetsetter              1.0
1                               fresh sugar jetsetter              1.0
2                               fresh sugar jetsetter              1.0
0   olehenriksen glow brightly - radiance-boosting...              0.0
..                                                ...              ...
15     the ordinary natural moisturizing factors + ha              2.0
16     the ordinary natural moisturizing factors + ha              2.0
17     the ordinary natural moisturizing factors + ha              2.0
18     the ordinary natural moisturizing factors + ha              2.0
19     the ordinary natural moisturizing factors + ha              2.0
20     the ordinary natural moisturizing factors + ha              2.0
21     the ordinary natural moisturizing factors + ha              2.0
22     the ordinary natural moisturizing factors + ha              2.0
23     the ordinary natural moisturizing factors + ha              2.0
24     the ordinary natural moisturizing factors + ha              2.0
25     the ordinary natural moisturizing factors + ha              1.0
26     the ordinary natural moisturizing factors + ha              1.0
27     the ordinary natural moisturizing factors + ha              1.0
28     the ordinary natural moisturizing factors + ha              1.0
29     the ordinary natural moisturizing factors + ha              1.0
30     the ordinary natural moisturizing factors + ha              1.0
31     the ordinary natural moisturizing factors + ha              1.0
32     the ordinary natural moisturizing factors + ha              1.0
33     the ordinary natural moisturizing factors + ha              1.0
34     the ordinary natural moisturizing factors + ha              1.0
35     the ordinary natural moisturizing factors + ha              1.0
36     the ordinary natural moisturizing factors + ha              1.0
37     the ordinary natural moisturizing factors + ha              1.0
38     the ordinary natural moisturizing factors + ha              1.0
39     the ordinary natural moisturizing factors + ha            

In [829]:
test['Times Mentioned'] = test_2['Times Mentioned']

In [830]:
test.head()

Product Name  Sephora?  \
0                  dr. jart+ mask heroes face savers         1   
0  moon juice beauty shroom vegan collagen protec...         1   
0   moon juice beauty shroom exfoliating acid potion         1   
0                 sephora collection face mask magic         1   
1                 sephora collection face mask magic         1   

         Subreddit  Times Mentioned  
0              N/A              0.0  
0              N/A              0.0  
0  scacjdiscussion              1.0  
0  MakeupAddiction              3.0  
1  BeautyAddiction              2.0

In [831]:
test[test['Product Name'] == 'tylenol']

Product Name  Sephora?              Subreddit  Times Mentioned
0       tylenol         0              AskReddit          34257.0
1       tylenol         0                opiates           7479.0
2       tylenol         0              BabyBumps           7011.0
3       tylenol         0                  Drugs           4925.0
4       tylenol         0          todayilearned           4465.0
5       tylenol         0          beyondthebump           4236.0
6       tylenol         0                   news           4132.0
7       tylenol         0               politics           2708.0
8       tylenol         0                AskDocs           2460.0
9       tylenol         0        TwoXChromosomes           2405.0
10      tylenol         0              Parenting           2339.0
11      tylenol         0      explainlikeimfive           2310.0
12      tylenol         0                    WTF           2301.0
13      tylenol         0                  funny           2142.0
14      tylenol         0                science           2124.0
15      tylenol         0                   pics           2107.0
16      tylenol         0          AdviceAnimals           2097.0
17      tylenol         0                  trees           1978.0
18      tylenol         0            breakingmom           1678.0
19      tylenol         0                   IAmA           1626.0
20      tylenol         0                nursing           1526.0
21      tylenol         0              worldnews           1399.0
22      tylenol         0               migraine           1307.0
23      tylenol         0            ChronicPain           1304.0
24      tylenol         0                 kratom           1261.0
25      tylenol         0               AskWomen           1257.0
26      tylenol         0                 videos           1167.0
27      tylenol         0          CrohnsDisease           1074.0
28      tylenol         0            infertility           1049.0
29      tylenol         0  Random_Acts_Of_Amazon           1023.0
..          ...       ...                    ...              ...
70      tylenol         0           changemyview            397.0
71      tylenol         0                Anxiety            396.0
72      tylenol         0            Libertarian            369.0
73      tylenol         0             depression            368.0
74      tylenol         0                   keto            364.0
75      tylenol         0         asktransgender            359.0
76      tylenol         0         DarkNetMarkets            352.0
77      tylenol         0   TheGirlSurvivalGuide            350.0
78      tylenol         0    fffffffuuuuuuuuuuuu            336.0
79      tylenol         0                   ADHD            330.0
80      tylenol         0               steroids            330.0
81      tylenol         0                    ems            329.0
82      tylenol         0    raisedbynarcissists            323.0
83      tylenol         0     CasualConversation            317.0
84      tylenol         0         quittingkratom            314.0
85      tylenol         0            nottheonion            290.0
86      tylenol         0                bipolar            284.0
87      tylenol         0                    ftm            283.0
88      tylenol         0                   Endo            281.0
89      tylenol         0             Nootropics            276.0
90      tylenol         0                atheism            256.0
91      tylenol         0          YouShouldKnow            251.0
92      tylenol         0                running            242.0
93      tylenol         0   insanepeoplefacebook            240.0
94      tylenol         0           ttcafterloss            238.0
95      tylenol         0                  drunk            236.0
96      tylenol         0     BlackPeopleTwitter            235.0
97      tylenol         0                 Advice            233.0
98      tylenol         0                 g

In [807]:
test[test['Times Mentioned'] > 1000]

Product Name  Sephora?              Subreddit  \
0       origins our best of the best         1          pokemontrades   
0          dr. jart+ ceramidin cream         1            AsianBeauty   
0         dr. jart+ ceramidin liquid         1            AsianBeauty   
0        laneige water sleeping mask         0            AsianBeauty   
0                       differin gel         0      SkincareAddiction   
0                 benefit gimme brow         0        MakeupAddiction   
0   anastasia beverly hills brow wiz         0        MakeupAddiction   
0                            tylenol         0              AskReddit   
1                            tylenol         0                opiates   
2                            tylenol         0              BabyBumps   
3                            tylenol         0                  Drugs   
4                            tylenol         0          todayilearned   
5                            tylenol         0          beyondthebump   
6                            tylenol         0                   news   
7                            tylenol         0               politics   
8                            tylenol         0                AskDocs   
9                            tylenol         0        TwoXChromosomes   
10                           tylenol         0              Parenting   
11                           tylenol         0      explainlikeimfive   
12                           tylenol         0                    WTF   
13                           tylenol         0                  funny   
14                           tylenol         0                science   
15                           tylenol         0                   pics   
16                           tylenol         0          AdviceAnimals   
17                           tylenol         0                  trees   
18                           tylenol         0            breakingmom   
19                           tylenol         0                   IAmA   
20                           tylenol         0                nursing   
21                           tylenol         0              worldnews   
22                           tylenol         0               migraine   
23                           tylenol         0            ChronicPain   
24                           tylenol         0                 kratom   
25                           tylenol         0               AskWomen   
26                           tylenol         0                 videos   
27                           tylenol         0          CrohnsDisease   
28                           tylenol         0            infertility   
29                           tylenol         0  Random_Acts_Of_Amazon   
0                stratia liquid gold         0            AsianBeauty   
1                stratia liquid gold         0      SkincareAddiction   
0     laura mercier secret concealer         0        MakeupAddiction   

    Times Mentioned  
0            1997.0  
0            2302.0  
0            1591.0  
0            1917.0  
0            2556.0  
0            2351.0  
0            1333.0  
0           34257.0  
1            7479.0  
2            7011.0  
3            4925.0  
4            4465.0  
5            4236.0  
6            4132.0  
7            2708.0  
8            2460.0  
9            2405.0  
10           2339.0  
11           2310.0  
12           2301.0  
13           2142.0  
14           2124.0  
15           2107.0  
16           2097.0  
17           1978.0  
18           1678.0  
19           1626.0  
20           1526.0  
21           1399.0  
22           1307.0  
23           1304.0  
24           1261.0  
25           1257.0  
26           1167.0  
27           1074.0  
28           1049.0  
29           1023.0  
0            2405.0  
1            2389.0  
0            1052.0

In [923]:
test.sort_values(by = ['Times Mentioned'], ascending = False)

Sephora?  \
Product Name                                                   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
differin gel                                               0   
tylenol                                                    0   
tylenol                                                    0   
stratia liquid gold                                        0   
stratia liquid gold                                        0   
benefit gimme brow                                         0   
tylenol                                                    0   
tylenol                                                    0   
dr. jart+ ceramidin cream                                  1   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
tylenol                                                    0   
origins our best of the best                               1   
tylenol                                                    0   
laneige water sleeping mask                                0   
tylenol                                                    0   
tylenol                                                    0   
dr. jart+ ceramidin liquid                                 1   
tylenol                                                    0   
tylenol                                                    0   
...                                                      ...   
dr. barbara sturm baby & kids body cream                   0   
lancôme dual-ended fan brush 31                            0   
e.l.f. beautifully precise eyeshadow brush no. 201         0   
flawless by gabrielle union shine spray                    0   
garnier fructis moisture lock 10-in-1 rescue le...         0   
marulaoil rare oil perfecting hairspray                    0   
& other stories marble blush in coquille heat              0   
tenoverten summer trio                                     0   
ysl rouge volupté shine oil-in-stick in red in ...         0   
regime des fleurs freeworld parfum                         0   
herbivore rosewater hydration trio                         1   
clarisonic makeup blending stocking stuffer                1   
lancôme purifying & comforting duo                         1   
blithe inbetween hydro priming cream                       1   
j.one haart mermaid glow color lip balm                    1   
l'occitane holiday crackers set                            1   
welleco sleep welle fortified calming tea refill           1   
herbivore self love bath + body ritual kit                 1   
blithe inbetween instant glowing cream                     1   
welleco the nourishing protein travel set                  1   
blithe inbetween makeup prep essence                       1   
estée lauder protect + hydrate keep glowing wit...         1   
lancôme lifting & firming duo                              1   
oribe free styler working hairspray                        0   
carol’s daughter pracaxi nectar curl twisting c...         0   
welleco sleep welle fortified calming tea                  1   
creme of nature with argan oil perfect edges ex...         0   
clarisonic mia smart cleanse & uplift holiday g...         1   
fresh sugar sweetcase                                      1   
dr. jart+ mask heroes face savers                          1   

                   

In [941]:
test.loc['tylenol', ['Subreddit', 'Times Mentioned']]

Subreddit  Times Mentioned
Product Name                                        
tylenol                   AskReddit          34257.0
tylenol                     opiates           7479.0
tylenol                   BabyBumps           7011.0
tylenol                       Drugs           4925.0
tylenol               todayilearned           4465.0
tylenol               beyondthebump           4236.0
tylenol                        news           4132.0
tylenol                    politics           2708.0
tylenol                     AskDocs           2460.0
tylenol             TwoXChromosomes           2405.0
tylenol                   Parenting           2339.0
tylenol           explainlikeimfive           2310.0
tylenol                         WTF           2301.0
tylenol                       funny           2142.0
tylenol                     science           2124.0
tylenol                        pics           2107.0
tylenol               AdviceAnimals           2097.0
tylenol                       trees           1978.0
tylenol                 breakingmom           1678.0
tylenol                        IAmA           1626.0
tylenol                     nursing           1526.0
tylenol                   worldnews           1399.0
tylenol                    migraine           1307.0
tylenol                 ChronicPain           1304.0
tylenol                      kratom           1261.0
tylenol                    AskWomen           1257.0
tylenol                      videos           1167.0
tylenol               CrohnsDisease           1074.0
tylenol                 infertility           1049.0
tylenol       Random_Acts_Of_Amazon           1023.0
...                             ...              ...
tylenol                changemyview            397.0
tylenol                     Anxiety            396.0
tylenol                 Libertarian            369.0
tylenol                  depression            368.0
tylenol                        keto            364.0
tylenol              asktransgender            359.0
tylenol              DarkNetMarkets            352.0
tylenol        TheGirlSurvivalGuide            350.0
tylenol         fffffffuuuuuuuuuuuu            336.0
tylenol                        ADHD            330.0
tylenol                    steroids            330.0
tylenol                         ems            329.0
tylenol         raisedbynarcissists            323.0
tylenol          CasualConversation            317.0
tylenol              quittingkratom            314.0
tylenol                 nottheonion            290.0
tylenol                     bipolar            284.0
tylenol                         ftm            283.0
tylenol                        Endo            281.0
tylenol                  Nootropics            276.0
tylenol                     atheism            256.0
tylenol               YouShouldKnow            251.0
tylenol                     running            242.0
tylenol        insanepeoplefacebook            240.0
tylenol                ttcafterloss            238.0
tylenol                       drunk            236.0
tylenol          BlackPeopleTwitter            235.0
tylenol                      Advice            233.0
tylenol                      gaming            233.0
tylenol                     antiMLM            228.0

[100 rows x 2 columns]

In [943]:
test['Subreddit'].value_counts()

N/A                      287
MakeupAddiction          200
muacjdiscussion          160
SkincareAddiction        131
MakeupRehab              129
AsianBeauty              112
makeupexchange            98
BeautyBoxes               90
MUAontheCheap             86
PanPorn                   69
AskReddit                 64
AskWomen                  61
Makeup                    60
AustralianMakeup          57
femalefashionadvice       56
MakeupAddicts             56
MakeupAddictionCanada     49
BeautyAddiction           49
makeupflatlays            47
RandomActsofMakeup        46
BeautyGuruChatter         46
TwoXChromosomes           36
beauty                    35
beautytalkph              35
TheGirlSurvivalGuide      34
AsianBeautyAdvice         31
Indiemakeupandmore        30
OliveMUA                  29
scacjdiscussion           28
SkincareAddicts           26
                        ... 
u_sonaliikhannaa           1
DishonoredRP               1
cordcutters                1
LicensedforBea

In [863]:
test.set_index('Product Name', inplace=True)

In [864]:
test.head()

Sephora?        Subreddit  \
Product Name                                                                    
dr. jart+ mask heroes face savers                          1              N/A   
moon juice beauty shroom vegan collagen protection         1              N/A   
moon juice beauty shroom exfoliating acid potion           1  scacjdiscussion   
sephora collection face mask magic                         1  MakeupAddiction   
sephora collection face mask magic                         1  BeautyAddiction   

                                                    Times Mentioned  
Product Name                                                         
dr. jart+ mask heroes face savers                               0.0  
moon juice beauty shroom vegan collagen protection              0.0  
moon juice beauty shroom exfoliating acid potion                1.0  
sephora collection face mask magic                              3.0  
sephora collection face mask magic                              2.0

In [877]:
table = pivot_table(test, values='Times Mentioned', index=['Product Name', 'Subreddit','Sephora?'],
                    columns=['Subreddit'], aggfunc=np.sum)

In [878]:
table

Subreddit                                                                          1200isplenty  \
Product Name                                       Subreddit             Sephora?                 
 gucci bloom                                       AsianBeauty           0                  NaN   
                                                   AsianParentStories    0                  NaN   
                                                   AskMen                0                  NaN   
                                                   AskReddit             0                  NaN   
                                                   AskWomen              0                  NaN   
                                                   BPDlovedones          0                  NaN   
                                                   BeautyBoxes           0                  NaN   
                                                   CampHalfBloodRP       0                  NaN   
                                                   China                 0                  NaN   
                                                   DesignerReps          0                  NaN   
                                                   FashionReps           0                  NaN   
                                                   FashionRepsBST        0                  NaN   
                                                   FortNiteBR            0                  NaN   
                                                   Frisson               0                  NaN   
                                                   KotakuInAction        0                  NaN   
                                                   ListeningHeads        0                  NaN   
                                                   MNTrolls              0                  NaN   
                                                   MUAontheCheap         0                  NaN   
                                                   MakeUpExchangeEU      0                  NaN   
                                                   MakeupAddiction       0                  NaN   
                                                   MakeupAddictionCanada 0                  NaN   
                                                   MakeupRehab           0                  NaN   
                                                   MonsterHunter         0                  NaN   
                                                   MtF                   0                  NaN   
                                                   NetflixBestOf         0                  NaN   
                                                   Overwatch             0                  NaN   
                                                   PanPorn               0                  NaN   
                                                   PerfumeExchange       0                  NaN   
                                                   RepLadies             0                  NaN   
                                                   RepLadiesBST          0                  NaN   
...                                                                                         ...   
wet n wild megalast liquid catsuit matte lipstick  drugstoreMUA          0                  NaN   
                                                   femalefashionadvice   0                  NaN   
                                                   makeupexchange        0                  NaN   
                                                   muacirclejerk         0                  NaN   
                                                   muacjdiscussion       0                  NaN   
                                                   rupaulsdragrace       0                  NaN   
                                                   traaaaaaannnnnnnnnns  0                  NaN   
winky lux glimmer balm                  

In [879]:
table.reset_index('Sephora?')

Subreddit                                                                 Sephora?  \
Product Name                                       Subreddit                         
 gucci bloom                                       AsianBeauty                   0   
                                                   AsianParentStories            0   
                                                   AskMen                        0   
                                                   AskReddit                     0   
                                                   AskWomen                      0   
                                                   BPDlovedones                  0   
                                                   BeautyBoxes                   0   
                                                   CampHalfBloodRP               0   
                                                   China                         0   
                                                   DesignerReps                  0   
                                                   FashionReps                   0   
                                                   FashionRepsBST                0   
                                                   FortNiteBR                    0   
                                                   Frisson                       0   
                                                   KotakuInAction                0   
                                                   ListeningHeads                0   
                                                   MNTrolls                      0   
                                                   MUAontheCheap                 0   
                                                   MakeUpExchangeEU              0   
                                                   MakeupAddiction               0   
                                                   MakeupAddictionCanada         0   
                                                   MakeupRehab                   0   
                                                   MonsterHunter                 0   
                                                   MtF                           0   
                                                   NetflixBestOf                 0   
                                                   Overwatch                     0   
                                                   PanPorn                       0   
                                                   PerfumeExchange               0   
                                                   RepLadies                     0   
                                                   RepLadiesBST                  0   
...                                                                            ...   
wet n wild megalast liquid catsuit matte lipstick  drugstoreMUA                  0   
                                                   femalefashionadvice           0   
                                                   makeupexchange                0   
                                                   muacirclejerk                 0   
                                                   muacjdiscussion               0   
                                                   rupaulsdragrace               0   
                                                   traaaaaaannnnnnnnnns          0   
winky lux glimmer balm                             N/A                           1   
youth to the people super glow hydration duo       N/A                           1   
ysl rouge volupté shine oil-in-stick in red in ... N/A                           0   
ysl tatouage couture matte stain in 7              BeautyGuruChatter             0   
                                                   MUAontheCheap                 0   
                                                   makeupflatlays                0   
yves saint laurent black opium cracker gift 

In [880]:
table.max()

Subreddit
1200isplenty              1.0
2007scape                 2.0
30PlusSkinCare           42.0
3DS                       1.0
40kLore                   2.0
42xcirclejerk             1.0
52MakeupThemes            1.0
52weeksofbaking           2.0
52weeksofcooking          3.0
80smusic                  1.0
90daysgoal                3.0
ABCDesis                  1.0
ABEFlair                  1.0
ABraThatFits              1.0
ADHD                    330.0
AFL                       1.0
AIPCTSHOP                 1.0
AMA                       2.0
AMAAggregator             1.0
AboveandBeyond            4.0
Accutane                 19.0
Adelaide                  1.0
Adoption                 21.0
AdvancedAsianBeauty       2.0
Advice                  233.0
AdviceAnimals          2097.0
AirBnB                    1.0
AllThingsTerran           1.0
Allergies                 1.0
AlternateHistory          1.0
                        ...  
vegetarian                2.0
videos                 1167.0


In [920]:
table.to_csv('./CSVs/FINAL_ONE_again.csv')

In [341]:
import matplotlib.pyplot as plt

from sklearn.decomposition import PCA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis

In [882]:
table.fillna(0, inplace = True)

In [883]:
table.head()

Subreddit                                 1200isplenty  2007scape  \
Product Name Subreddit          Sephora?                            
 gucci bloom AsianBeauty        0                  0.0        0.0   
             AsianParentStories 0                  0.0        0.0   
             AskMen             0                  0.0        0.0   
             AskReddit          0                  0.0        0.0   
             AskWomen           0                  0.0        0.0   

Subreddit                                 30PlusSkinCare  3DS  40kLore  \
Product Name Subreddit          Sephora?                                 
 gucci bloom AsianBeauty        0                    0.0  0.0      0.0   
             AsianParentStories 0                    0.0  0.0      0.0   
             AskMen             0                    0.0  0.0      0.0   
             AskReddit          0                    0.0  0.0      0.0   
             AskWomen           0                    0.0  0.0      0.0   

Subreddit                                 42xcirclejerk  52MakeupThemes  \
Product Name Subreddit          Sephora?                                  
 gucci bloom AsianBeauty        0                   0.0             0.0   
             AsianParentStories 0                   0.0             0.0   
             AskMen             0                   0.0             0.0   
             AskReddit          0                   0.0             0.0   
             AskWomen           0                   0.0             0.0   

Subreddit                                 52weeksofbaking  52weeksofcooking  \
Product Name Subreddit          Sephora?                                      
 gucci bloom AsianBeauty        0                     0.0               0.0   
             AsianParentStories 0                     0.0               0.0   
             AskMen             0                     0.0               0.0   
             AskReddit          0                     0.0               0.0   
             AskWomen           0                     0.0               0.0   

Subreddit                                 80smusic    ...     writing  \
Product Name Subreddit          Sephora?              ...               
 gucci bloom AsianBeauty        0              0.0    ...         0.0   
             AsianParentStories 0              0.0    ...         0.0   
             AskMen             0              0.0    ...         0.0   
             AskReddit          0              0.0    ...         0.0   
             AskWomen           0              0.0    ...         0.0   

Subreddit                                 wroteabook  wsgy  xovainexpats  \
Product Name Subreddit          Sephora?                                   
 gucci bloom AsianBeauty        0                0.0   0.0           0.0   
             AsianParentStories 0                0.0   0.0           0.0   
             AskMen             0                0.0   0.0           0.0   
             AskReddit          0                0.0   0.0           0.0   
             AskWomen           0                0.0   0.0           0.0   

Subreddit                                 xxfitness  xxketo  youngMUA  yugioh  \
Product Name Subreddit          Sephora?                                        
 gucci bloom AsianBeauty        0               0.0     0.0       0.0     0.0   
             AsianParentStories 0               0.0     0.0       0.0     0.0   
             AskMen             0               0.0     0.0       0.0     0.0   
             AskReddit          0               0.0     0.0       0.0     0.0   
             AskWomen           0               0.0     0.0       0.0     0.0   

Subreddit                                 zen  zerocarb  
Product Name Subreddit          Sephora?                 
 gucci bloom AsianBeauty        0         0.0       0.0  
             AsianParentStories 0         0.0       0.0  
             AskMen             0         0.0       0.0  
             A

In [888]:
table.loc[table.index.get_level_values('Product Name') == 'tylenol'].sum()

Subreddit
1200isplenty              0.0
2007scape                 0.0
30PlusSkinCare            0.0
3DS                       0.0
40kLore                   0.0
42xcirclejerk             0.0
52MakeupThemes            0.0
52weeksofbaking           0.0
52weeksofcooking          0.0
80smusic                  0.0
90daysgoal                0.0
ABCDesis                  0.0
ABEFlair                  0.0
ABraThatFits              0.0
ADHD                    330.0
AFL                       0.0
AIPCTSHOP                 0.0
AMA                       0.0
AMAAggregator             0.0
AboveandBeyond            0.0
Accutane                  0.0
Adelaide                  0.0
Adoption                  0.0
AdvancedAsianBeauty       0.0
Advice                  233.0
AdviceAnimals          2097.0
AirBnB                    0.0
AllThingsTerran           0.0
Allergies                 0.0
AlternateHistory          0.0
                        ...  
vegetarian                0.0
videos                 1167.0


In [890]:
table.head()

Subreddit                                 1200isplenty  2007scape  \
Product Name Subreddit          Sephora?                            
 gucci bloom AsianBeauty        0                  0.0        0.0   
             AsianParentStories 0                  0.0        0.0   
             AskMen             0                  0.0        0.0   
             AskReddit          0                  0.0        0.0   
             AskWomen           0                  0.0        0.0   

Subreddit                                 30PlusSkinCare  3DS  40kLore  \
Product Name Subreddit          Sephora?                                 
 gucci bloom AsianBeauty        0                    0.0  0.0      0.0   
             AsianParentStories 0                    0.0  0.0      0.0   
             AskMen             0                    0.0  0.0      0.0   
             AskReddit          0                    0.0  0.0      0.0   
             AskWomen           0                    0.0  0.0      0.0   

Subreddit                                 42xcirclejerk  52MakeupThemes  \
Product Name Subreddit          Sephora?                                  
 gucci bloom AsianBeauty        0                   0.0             0.0   
             AsianParentStories 0                   0.0             0.0   
             AskMen             0                   0.0             0.0   
             AskReddit          0                   0.0             0.0   
             AskWomen           0                   0.0             0.0   

Subreddit                                 52weeksofbaking  52weeksofcooking  \
Product Name Subreddit          Sephora?                                      
 gucci bloom AsianBeauty        0                     0.0               0.0   
             AsianParentStories 0                     0.0               0.0   
             AskMen             0                     0.0               0.0   
             AskReddit          0                     0.0               0.0   
             AskWomen           0                     0.0               0.0   

Subreddit                                 80smusic    ...     writing  \
Product Name Subreddit          Sephora?              ...               
 gucci bloom AsianBeauty        0              0.0    ...         0.0   
             AsianParentStories 0              0.0    ...         0.0   
             AskMen             0              0.0    ...         0.0   
             AskReddit          0              0.0    ...         0.0   
             AskWomen           0              0.0    ...         0.0   

Subreddit                                 wroteabook  wsgy  xovainexpats  \
Product Name Subreddit          Sephora?                                   
 gucci bloom AsianBeauty        0                0.0   0.0           0.0   
             AsianParentStories 0                0.0   0.0           0.0   
             AskMen             0                0.0   0.0           0.0   
             AskReddit          0                0.0   0.0           0.0   
             AskWomen           0                0.0   0.0           0.0   

Subreddit                                 xxfitness  xxketo  youngMUA  yugioh  \
Product Name Subreddit          Sephora?                                        
 gucci bloom AsianBeauty        0               0.0     0.0       0.0     0.0   
             AsianParentStories 0               0.0     0.0       0.0     0.0   
             AskMen             0               0.0     0.0       0.0     0.0   
             AskReddit          0               0.0     0.0       0.0     0.0   
             AskWomen           0               0.0     0.0       0.0     0.0   

Subreddit                                 zen  zerocarb  
Product Name Subreddit          Sephora?                 
 gucci bloom AsianBeauty        0         0.0       0.0  
             AsianParentStories 0         0.0       0.0  
             AskMen             0         0.0       0.0  
             A

In [948]:
table['Kanye'].max()

4.0

In [892]:
table = table.reset_index('Sephora?')

In [893]:
table.head()

Subreddit                        Sephora?  1200isplenty  2007scape  \
Product Name Subreddit                                               
 gucci bloom AsianBeauty                0           0.0        0.0   
             AsianParentStories         0           0.0        0.0   
             AskMen                     0           0.0        0.0   
             AskReddit                  0           0.0        0.0   
             AskWomen                   0           0.0        0.0   

Subreddit                        30PlusSkinCare  3DS  40kLore  42xcirclejerk  \
Product Name Subreddit                                                         
 gucci bloom AsianBeauty                    0.0  0.0      0.0            0.0   
             AsianParentStories             0.0  0.0      0.0            0.0   
             AskMen                         0.0  0.0      0.0            0.0   
             AskReddit                      0.0  0.0      0.0            0.0   
             AskWomen                       0.0  0.0      0.0            0.0   

Subreddit                        52MakeupThemes  52weeksofbaking  \
Product Name Subreddit                                             
 gucci bloom AsianBeauty                    0.0              0.0   
             AsianParentStories             0.0              0.0   
             AskMen                         0.0              0.0   
             AskReddit                      0.0              0.0   
             AskWomen                       0.0              0.0   

Subreddit                        52weeksofcooking    ...     writing  \
Product Name Subreddit                               ...               
 gucci bloom AsianBeauty                      0.0    ...         0.0   
             AsianParentStories               0.0    ...         0.0   
             AskMen                           0.0    ...         0.0   
             AskReddit                        0.0    ...         0.0   
             AskWomen                         0.0    ...         0.0   

Subreddit                        wroteabook  wsgy  xovainexpats  xxfitness  \
Product Name Subreddit                                                       
 gucci bloom AsianBeauty                0.0   0.0           0.0        0.0   
             AsianParentStories         0.0   0.0           0.0        0.0   
             AskMen                     0.0   0.0           0.0        0.0   
             AskReddit                  0.0   0.0           0.0        0.0   
             AskWomen                   0.0   0.0           0.0        0.0   

Subreddit                        xxketo  youngMUA  yugioh  zen  zerocarb  
Product Name Subreddit                                                    
 gucci bloom AsianBeauty            0.0       0.0     0.0  0.0       0.0  
             AsianParentStories     0.0       0.0     0.0  0.0       0.0  
             AskMen                 0.0       0.0     0.0  0.0       0.0  
             AskReddit              0.0       0.0     0.0  0.0       0.0  
             AskWomen               0.0       0.0     0.0  0.0       0.0  

[5 rows x 1130 columns]

In [919]:
table.shape

(4926, 1130)

In [894]:
nc = [x for x in table.columns if x != 'Sephora?']
X = table[nc]
y = table['Sephora?']

In [895]:
X_train, X_test, y_train, y_test = train_test_split(X, y)

In [896]:
from sklearn.linear_model import LogisticRegression

In [949]:
X

Subreddit                                                                 1200isplenty  \
Product Name                                       Subreddit                             
 gucci bloom                                       AsianBeauty                     0.0   
                                                   AsianParentStories              0.0   
                                                   AskMen                          0.0   
                                                   AskReddit                       0.0   
                                                   AskWomen                        0.0   
                                                   BPDlovedones                    0.0   
                                                   BeautyBoxes                     0.0   
                                                   CampHalfBloodRP                 0.0   
                                                   China                           0.0   
                                                   DesignerReps                    0.0   
                                                   FashionReps                     0.0   
                                                   FashionRepsBST                  0.0   
                                                   FortNiteBR                      0.0   
                                                   Frisson                         0.0   
                                                   KotakuInAction                  0.0   
                                                   ListeningHeads                  0.0   
                                                   MNTrolls                        0.0   
                                                   MUAontheCheap                   0.0   
                                                   MakeUpExchangeEU                0.0   
                                                   MakeupAddiction                 0.0   
                                                   MakeupAddictionCanada           0.0   
                                                   MakeupRehab                     0.0   
                                                   MonsterHunter                   0.0   
                                                   MtF                             0.0   
                                                   NetflixBestOf                   0.0   
                                                   Overwatch                       0.0   
                                                   PanPorn                         0.0   
                                                   PerfumeExchange                 0.0   
                                                   RepLadies                       0.0   
                                                   RepLadiesBST                    0.0   
...                                                                                ...   
wet n wild megalast liquid catsuit matte lipstick  drugstoreMUA                    0.0   
                                                   femalefashionadvice             0.0   
                                                   makeupexchange                  0.0   
                                                   muacirclejerk                   0.0   
                                                   muacjdiscussion                 0.0   
                                                   rupaulsdragrace                 0.0   
                                                   traaaaaaannnnnnnnnns            0.0   
winky lux glimmer balm                             N/A                             0.0   
youth to the people super glow hydration duo       N/A                             0.0   
ysl rouge volupté shine oil-in-stick in red in ... N/A                             0.0   
ysl tatouage couture matte stain in 7              BeautyGuruChatter               0.0   
                                        

In [918]:
y.sum()

1808

In [898]:
lr = LogisticRegression()
model = lr.fit(X_train, y_train)

print(lr.score(X_test, y_test))

0.6306818181818182


In [899]:
print('Logreg intercept:', lr.intercept_)
print('Logreg coef(s):', lr.coef_)

Logreg intercept: [-0.45278917]
Logreg coef(s): [[ 0.00446031  0.00445642 -0.00675743 ... -0.0016013  -0.00320111
  -0.0016013 ]]


In [900]:
from sklearn.model_selection import GridSearchCV

gs_params = {
    'penalty':['l1','l2'],
    'solver':['liblinear'],
    'C':np.logspace(-5,0,100)
}

lr_gridsearch = GridSearchCV(LogisticRegression(), gs_params, cv=5, verbose=1)

In [901]:
%%time
lr_gridsearch = lr_gridsearch.fit(X_train, y_train)

Fitting 5 folds for each of 200 candidates, totalling 1000 fits
CPU times: user 4min 21s, sys: 1min 3s, total: 5min 24s
Wall time: 1min 30s


[Parallel(n_jobs=1)]: Done 1000 out of 1000 | elapsed:  1.5min finished


In [902]:
lr_gridsearch.best_score_

0.6478072550081213

In [903]:
lr_gridsearch.best_params_

{'C': 0.8902150854450392, 'penalty': 'l1', 'solver': 'liblinear'}

In [904]:
best_lr = lr_gridsearch.best_estimator_

In [905]:
best_lr.score(X_test, y_test)

0.6469155844155844

In [906]:
best_lr.classes_

array([0, 1])

In [908]:
X.columns

Index(['1200isplenty', '2007scape', '30PlusSkinCare', '3DS', '40kLore',
       '42xcirclejerk', '52MakeupThemes', '52weeksofbaking',
       '52weeksofcooking', '80smusic',
       ...
       'writing', 'wroteabook', 'wsgy', 'xovainexpats', 'xxfitness', 'xxketo',
       'youngMUA', 'yugioh', 'zen', 'zerocarb'],
      dtype='object', name='Subreddit', length=1129)

In [909]:
coef_df.shape

(1129, 3)

In [910]:
coef_df = pd.DataFrame()
coef_df = pd.DataFrame({
        'coef': best_lr.coef_[0],
        'feature': X.columns
    })

coef_df['abs_coef'] = np.abs(coef_df.coef)

# sort by absolute value of coefficient (magnitude)
coef_df.sort_values('abs_coef', ascending=False, inplace=True)

In [945]:
coef_df[coef_df.coef > 0].head(25)

coef           feature  abs_coef
494   1.738603           Sephora  1.738603
25    1.097647     AdviceAnimals  1.097647
1109  1.009943       whowouldwin  1.009943
839   0.965673              infj  0.965673
89    0.880516            Baking  0.880516
194   0.762550             DotA2  0.762550
246   0.762550            Frugal  0.762550
1100  0.740529            videos  0.740529
946   0.703482   personalfinance  0.703482
1099  0.696403        vegetarian  0.696403
8     0.661456  52weeksofcooking  0.661456
851   0.607187       ketorecipes  0.607187
823   0.584524              h1z1  0.584524
304   0.576428            Israel  0.576428
718   0.576357         copypasta  0.576357
294   0.576357       IndiaSpeaks  0.576357
917   0.552310              news  0.552310
1034  0.526791               tea  0.526791
312   0.526736             Kanye  0.526736
695   0.526736        budgetfood  0.526736
1043  0.526736               tf2  0.526736
683   0.522864        boardgames  0.522864
589   0.510817               WTF  0.510817
1048  0.493060    tonightsdinner  0.493060
220   0.477962        FanFiction  0.477962

In [953]:
coef_df[coef_df.coef == 0].head(30)

coef               feature  abs_coef
747   0.0    dontdeadopeninside       0.0
852   0.0           ketoscience       0.0
77    0.0        AustralianHair       0.0
850   0.0                ketonz       0.0
76    0.0            Australia_       0.0
854   0.0                 kings       0.0
103   0.0             BlackHair       0.0
855   0.0                kohtao       0.0
856   0.0               konmari       0.0
885   0.0             marathons       0.0
68    0.0        AskWomenOver30       0.0
69    0.0            Assistance       0.0
880   0.0           malefashion       0.0
70    0.0      AstralProjection       0.0
71    0.0               Atlanta       0.0
741   0.0    depressionregimens       0.0
875   0.0                   mac       0.0
874   0.0                 lupus       0.0
72    0.0     AugustBumpers2017       0.0
872   0.0          lookoftheday       0.0
742   0.0              diabetes       0.0
871   0.0              longhair       0.0
870   0.0                london       0.0
869   0.0          listentothis       0.0
868   0.0             lifehacks       0.0
743   0.0                 dmmmb       0.0
867   0.0                  lido       0.0
866   0.0     lewronggeneration       0.0
744   0.0               dndnext       0.0
865   0.0  lesbianfashionadvice       0.0

In [951]:
coef_df[coef_df.coef != 0].head(50)

coef              feature  abs_coef
494   1.738603              Sephora  1.738603
275  -1.618787      HaircareScience  1.618787
751  -1.401101         drugstoreMUA  1.401101
271  -1.285036                 Hair  1.285036
643  -1.201720       asktransgender  1.201720
730  -1.100146            curlyhair  1.100146
25    1.097647        AdviceAnimals  1.097647
221  -1.086032       FancyFollicles  1.086032
1109  1.009943          whowouldwin  1.009943
626  -1.009271              amiugly  1.009271
839   0.965673                 infj  0.965673
586  -0.959564          VeganBeauty  0.959564
20   -0.947243             Accutane  0.947243
283  -0.923411           HoodedEyes  0.923411
89    0.880516               Baking  0.880516
883  -0.799147       malehairadvice  0.799147
350  -0.799030              MakEnts  0.799030
382  -0.786390                  MtF  0.786390
663  -0.780710               beauty  0.780710
359  -0.778861      MakeupEducation  0.778861
560  -0.775442    TrollXChromosomes  0.775442
194   0.762550                DotA2  0.762550
246   0.762550               Frugal  0.762550
200  -0.754583                  EDC  0.754583
352  -0.741435     MakeUpExchangeEU  0.741435
1100  0.740529               videos  0.740529
226  -0.703536  FeminineNotFeminist  0.703536
946   0.703482      personalfinance  0.703482
1099  0.696403           vegetarian  0.696403
1110 -0.689208          wicked_edge  0.689208
8     0.661456     52weeksofcooking  0.661456
662  -0.625861               beards  0.625861
851   0.607187          ketorecipes  0.607187
427  -0.600765          Philippines  0.600765
479  -0.592360              Rosacea  0.592360
661  -0.588282           bbexchange  0.588282
823   0.584524                 h1z1  0.584524
380  -0.577479        MonolidMakeup  0.577479
1061 -0.577352            tressless  0.577352
504  -0.577350       Showerthoughts  0.577350
304   0.576428               Israel  0.576428
718   0.576357            copypasta  0.576357
294   0.576357          IndiaSpeaks  0.576357
778  -0.568175     femalehairadvice  0.568175
653  -0.567619        awfuleyebrows  0.567619
917   0.552310                 news  0.552310
1034  0.526791                  tea  0.526791
312   0.526736                Kanye  0.526736
695   0.526736           budgetfood  0.526736
1043  0.526736                  tf2  0.526736

In [914]:
print('Logreg predicted probabilities:', lr.predict(X_train.head(5)))

Logreg predicted probabilities: [0 0 0 0 0]


In [915]:
print('Logreg predicted probabilities:', lr.predict_proba(X_train.head(5)))

Logreg predicted probabilities: [[0.60918229 0.39081771]
 [0.62109719 0.37890281]
 [0.62033091 0.37966909]
 [0.61085284 0.38914716]
 [0.61133078 0.38866922]]


In [916]:
y_hat = lr_gridsearch.predict(X_train)
y_hat_proba = lr_gridsearch.predict_proba(X_train)

X.loc[:, 'actual_y'] = y
X.loc[:, 'predicted_label'] = y_hat
X.loc[:, 'predicted_proba'] = y_hat_proba[:, 1]

X.head()

ValueError: cannot set using a multi-index selection indexer with a different length than the value

In [242]:
Subreddit = df_final[['Subreddit', 'Times Mentioned']].apply(pd.Series)

# rename each variable is tags
#Subreddit = Subreddit.rename(columns = lambda x : 'tag_' + str(x))

# view the tags dataframe
Subreddit

Subreddit  \
Product Name                                                                                            
dr. jart+ mask heroes face savers                                                                None   
moon juice beauty shroom vegan collagen protection                                               None   
moon juice beauty shroom exfoliating acid potion                                    [scacjdiscussion]   
sephora collection face mask magic                  [MakeupAddiction, BeautyAddiction, AsianBeauty...   
laneige kiss and make up set                        [AsianBeauty, AsianBeautyAdvice, SkincareAddic...   
drunk elephant agent ellie day kit                                                    [MUAontheCheap]   
olehenriksen glow cycle retin-alt power serum                                       [muacjdiscussion]   
welleco the super elixir                            [SkincareAddiction, BeautyBoxes, TheColorIsRed...   
la mer merry little miracles                                                          [MUAontheCheap]   
drunk elephant inspector drunk night kit                                                         None   
sol de janeiro bum bum carnaval extravaganza                                                     None   
tatcha skincare for makeup lovers obento box        [AsianBeautyRehab, MakeupAddiction, MakeupAddi...   
fresh sugar jetsetter                                    [cocktails, makeupflatlays, muacjdiscussion]   
olehenriksen glow brightly - radiance-boosting ...                                               None   
farmacy honeymoon glow aha resurfacing night se...                                    [MUAontheCheap]   
drunk elephant the big reveal kit                                                                None   
herbivore jade facial roller                                                      [SkincareAddiction]   
summer fridays overtime mask                                                      [SkincareAddiction]   
fresh sky high-dration                                                                           None   
sunday riley good genes holiday kit                 [MakeupAddictionCanada, AsianBeauty, MakeupAdd...   
fresh destination sugar                             [AskReddit, WritingPrompts, loseit, Scotch, wo...   
algenist secrets of algae kit                                                                    None   
peter thomas roth mask frenzy                              [MakeupAddictionCanada, SkincareAddiction]   
olehenriksen goodnight glow retin-alt sleeping ...                                               None   
kiehl's since 1851 brighten up & glow                                                            None   
caudalie brightening heroes                                                                      None   
laneige sleep and glow set                          [MakeupAddictionCanada, PanPorn, SkincareAddic...   
origins our best of the best                        [pokemontrades, atheism, AskReddit, Christiani...   
fresh ready, set, firm                              [WritingPrompts, AskReddit, food, Cooking, veg...   
tatcha bestsellers set                              [MakeupAddiction, AsianBeautyAdvice, Makeup, S...   
...                                                                                               ...   
renée rouleau redness care serum                                                  [SkincareAddiction]   
eminence calm skin arnica masque                    [SkincareAddiction, MakeupAddiction, femalefas...   
bioderma sensibio deo anti-perspirant                                                            None   
stratia liquid gold                                 [AsianBeauty, SkincareAddiction, asianbeautyex...   
kimiko super fine eyebrow pencil in coffee                                          [MakeupAddiction]   
donni silk chiquita scrunchie                                                                    None 

In [255]:
df_final.loc['laneige kiss and make up set','Subreddit']

['AsianBeauty', 'AsianBeautyAdvice', 'SkincareAddiction', 'abdiscussion']

In [270]:
df_final.reset_index(inplace=True)
rows = []
_ = df_final.apply(lambda row: [rows.append([row['Product Name'], row['Times Mentioned'], nn]) 
                         for nn in row.Subreddit], axis=1)
df_new = pd.DataFrame(rows, columns=df_final.columns).set_index(['Product Name', 'Times Mentioned'])    

TypeError: ("'NoneType' object is not iterable", 'occurred at index 0')

In [256]:
for i in df_final['Subreddit']:
    print(i.str)

None
None
['scacjdiscussion']
['MakeupAddiction', 'BeautyAddiction', 'AsianBeauty', 'AustralianMakeup', 'FeminineNotFeminist', 'MakeupRehab']
['AsianBeauty', 'AsianBeautyAdvice', 'SkincareAddiction', 'abdiscussion']
['MUAontheCheap']
['muacjdiscussion']
['SkincareAddiction', 'BeautyBoxes', 'TheColorIsRed', 'eczema', 'veganfitness']
['MUAontheCheap']
None
None
['AsianBeautyRehab', 'MakeupAddiction', 'MakeupAddictionCanada']
['cocktails', 'makeupflatlays', 'muacjdiscussion']
None
['MUAontheCheap']
None
['SkincareAddiction']
['SkincareAddiction']
None
['MakeupAddictionCanada', 'AsianBeauty', 'MakeupAddiction', 'MUAontheCheap', 'MakeupRehab', 'Sephora']
['AskReddit', 'WritingPrompts', 'loseit', 'Scotch', 'worldbuilding', '3DS', '90daysgoal', 'AMA', 'AdviceAnimals', 'AirBnB', 'AskCulinary', 'AskFoodHistorians', 'AskHistorians', 'Australia_', 'AutoNewspaper', 'Baking', 'CasualConversation', 'Colombia', 'DaystromInstitute', 'Detroit', 'HoustonBeer', 'Israel', 'KeepWriting', 'LoLFanArt', 'Oliv

In [238]:
objs = [df_final, pd.DataFrame(df_final['Subreddit'].tolist())]
pd.concat(objs, axis=1)#.drop('samples', axis=1)

/Users/emmaeleanoryork/anaconda3/lib/python3.6/site-packages/pandas/core/indexes/api.py:107: RuntimeWarning: '<' not supported between instances of 'str' and 'int', sort order is undefined for incomparable objects
  result = result.union(other)


Subreddit  \
dr. jart+ mask heroes face savers                                                                None   
moon juice beauty shroom vegan collagen protection                                               None   
moon juice beauty shroom exfoliating acid potion                                    [scacjdiscussion]   
sephora collection face mask magic                  [MakeupAddiction, BeautyAddiction, AsianBeauty...   
laneige kiss and make up set                        [AsianBeauty, AsianBeautyAdvice, SkincareAddic...   
drunk elephant agent ellie day kit                                                    [MUAontheCheap]   
olehenriksen glow cycle retin-alt power serum                                       [muacjdiscussion]   
welleco the super elixir                            [SkincareAddiction, BeautyBoxes, TheColorIsRed...   
la mer merry little miracles                                                          [MUAontheCheap]   
drunk elephant inspector drunk night kit                                                         None   
sol de janeiro bum bum carnaval extravaganza                                                     None   
tatcha skincare for makeup lovers obento box        [AsianBeautyRehab, MakeupAddiction, MakeupAddi...   
fresh sugar jetsetter                                    [cocktails, makeupflatlays, muacjdiscussion]   
olehenriksen glow brightly - radiance-boosting ...                                               None   
farmacy honeymoon glow aha resurfacing night se...                                    [MUAontheCheap]   
drunk elephant the big reveal kit                                                                None   
herbivore jade facial roller                                                      [SkincareAddiction]   
summer fridays overtime mask                                                      [SkincareAddiction]   
fresh sky high-dration                                                                           None   
sunday riley good genes holiday kit                 [MakeupAddictionCanada, AsianBeauty, MakeupAdd...   
fresh destination sugar                             [AskReddit, WritingPrompts, loseit, Scotch, wo...   
algenist secrets of algae kit                                                                    None   
peter thomas roth mask frenzy                              [MakeupAddictionCanada, SkincareAddiction]   
olehenriksen goodnight glow retin-alt sleeping ...                                               None   
kiehl's since 1851 brighten up & glow                                                            None   
caudalie brightening heroes                                                                      None   
laneige sleep and glow set                          [MakeupAddictionCanada, PanPorn, SkincareAddic...   
origins our best of the best                        [pokemontrades, atheism, AskReddit, Christiani...   
fresh ready, set, firm                              [WritingPrompts, AskReddit, food, Cooking, veg...   
tatcha bestsellers set                              [MakeupAddiction, AsianBeautyAdvice, Makeup, S...   
...                                                                                               ...   
624                                                                                               NaN   
625                                                                                               NaN   
626                                                                                               NaN   
627                                                                                               NaN   
628                                                                                               NaN   
629                                                                                               NaN   
630                                                                                               NaN 

pandas.core.series.Series

In [234]:
df_final.Subreddit.apply(pd.series).stack()

AttributeError: module 'pandas' has no attribute 'series'

In [214]:
df = pd.DataFrame(dict(A=list('ab'), B=[1, 2], C=[[1, 2, 3], [4, 5, 6]], ))
df

A  B          C
0  a  1  [1, 2, 3]
1  b  2  [4, 5, 6]

In [215]:
df.set_index(['A', 'B']).C.apply(pd.Series).stack().reset_index(['A', 'B'], name='C')

A  B  C
0  a  1  1
1  a  1  2
2  a  1  3
0  b  2  4
1  b  2  5
2  b  2  6

In [ ]:
names = ['A', 'B']
idx = pd.MultiIndex.from_tuples(df[names].values.tolist(), names=names)
pd.DataFrame(df.C.tolist(), idx).stack().reset_index(names, name='C')

In [ ]:
names = ['Product Name']
idx = pd.

In [230]:

df_final.set_index(['Product Name', 'Sephora?'])['Subreddit'].apply(pd.Series).stack().reset_index(['Product Name', 'Sephora?'], name = 'Subreddit')

Product Name  Sephora?  \
0    moon juice beauty shroom exfoliating acid potion         1   
0                  sephora collection face mask magic         1   
1                  sephora collection face mask magic         1   
2                  sephora collection face mask magic         1   
3                  sephora collection face mask magic         1   
4                  sephora collection face mask magic         1   
5                  sephora collection face mask magic         1   
0                        laneige kiss and make up set         1   
1                        laneige kiss and make up set         1   
2                        laneige kiss and make up set         1   
3                        laneige kiss and make up set         1   
0                  drunk elephant agent ellie day kit         1   
0       olehenriksen glow cycle retin-alt power serum         1   
0                            welleco the super elixir         1   
1                            welleco the super elixir         1   
2                            welleco the super elixir         1   
3                            welleco the super elixir         1   
4                            welleco the super elixir         1   
0                        la mer merry little miracles         1   
0        tatcha skincare for makeup lovers obento box         1   
1        tatcha skincare for makeup lovers obento box         1   
2        tatcha skincare for makeup lovers obento box         1   
0                               fresh sugar jetsetter         1   
1                               fresh sugar jetsetter         1   
2                               fresh sugar jetsetter         1   
0   farmacy honeymoon glow aha resurfacing night s...         1   
0                        herbivore jade facial roller         1   
0                        summer fridays overtime mask         1   
0                 sunday riley good genes holiday kit         1   
1                 sunday riley good genes holiday kit         1   
..                                                ...       ...   
15     the ordinary natural moisturizing factors + ha         0   
16     the ordinary natural moisturizing factors + ha         0   
17     the ordinary natural moisturizing factors + ha         0   
18     the ordinary natural moisturizing factors + ha         0   
19     the ordinary natural moisturizing factors + ha         0   
20     the ordinary natural moisturizing factors + ha         0   
21     the ordinary natural moisturizing factors + ha         0   
22     the ordinary natural moisturizing factors + ha         0   
23     the ordinary natural moisturizing factors + ha         0   
24     the ordinary natural moisturizing factors + ha         0   
25     the ordinary natural moisturizing factors + ha         0   
26     the ordinary natural moisturizing factors + ha         0   
27     the ordinary natural moisturizing factors + ha         0   
28     the ordinary natural moisturizing factors + ha         0   
29     the ordinary natural moisturizing factors + ha         0   
30     the ordinary natural moisturizing factors + ha         0   
31     the ordinary natural moisturizing factors + ha         0   
32     the ordinary natural moisturizing factors + ha         0   
33     the ordinary natural moisturizing factors + ha         0   
34     the ordinary natural moisturizing factors + ha         0   
35     the ordinary natural moisturizing factors + ha         0   
36     the ordinary natural moisturizing factors + ha         0   
37     the ordinary natural moisturizing factors + ha         0   
38     the ordinary natural moisturizing factors + ha         0   
39     the ordinary natural moisturizing factors + ha         0   
40     the ordinary natural moisturizing factors + ha         0   
41     the ordinary natural moisturizing factors + ha         0   
42     the ordinary natural moisturizing factors + ha         0   
43     the ordinary n

In [210]:
for r in range(df_final.shape[0]):
    if df_final.loc[r, 'Subreddit'] != None:
        for i in df_final.loc[r, 'Subreddit']:
            print(i)

scacjdiscussion
MakeupAddiction
BeautyAddiction
AsianBeauty
AustralianMakeup
FeminineNotFeminist
MakeupRehab
AsianBeauty
AsianBeautyAdvice
SkincareAddiction
abdiscussion
MUAontheCheap
muacjdiscussion
SkincareAddiction
BeautyBoxes
TheColorIsRed
eczema
veganfitness
MUAontheCheap
AsianBeautyRehab
MakeupAddiction
MakeupAddictionCanada
cocktails
makeupflatlays
muacjdiscussion
MUAontheCheap
SkincareAddiction
SkincareAddiction
MakeupAddictionCanada
AsianBeauty
MakeupAddiction
MUAontheCheap
MakeupRehab
Sephora
AskReddit
WritingPrompts
loseit
Scotch
worldbuilding
3DS
90daysgoal
AMA
AdviceAnimals
AirBnB
AskCulinary
AskFoodHistorians
AskHistorians
Australia_
AutoNewspaper
Baking
CasualConversation
Colombia
DaystromInstitute
Detroit
HoustonBeer
Israel
KeepWriting
LoLFanArt
OliveMUA
Random_Acts_Of_Amazon
SuicideWatch
TrueFilm
Winnipeg
arma
beards
beer
bodyweightfitness
bourbon
budgetfood
cigars
criminalminds
diabetes
explainlikeimfive
food
fullmoviesonanything
funny
germany
indianapolis
interesting

PaleMUA
PlasticSurgery
Rateme
RedPillWives
Rosacea
SkincareAddictionUK
SkincareRehab
TheMeteorSword
TrueSTL
TwoXChromosomes
ancientasianbeauty
breakingmom
gaysian
keto
korea
makeupflatlays
mcrendered
minimalism
nytimes
proED
rupaulsdragrace
slydigs
topofthemorning
uwaterloo
vegan
zerocarb
SkincareAddiction
AsianBeauty
30PlusSkinCare
MUAontheCheap
Skincare_Addiction
SkincareAddiction
AsianBeauty
MakeupAddiction
muacjdiscussion
AsianBeautyAdvice
AskTrollX
AusSkincare
BeautyBoxes
RandomActsofMakeup
Rosacea
SkincareAddicts
TwoXChromosomes
transtimelines
MUAontheCheap
SkincareAddiction
SkincareAddiction
AsianBeauty
acne
AskReddit
SkincareAddicts
tretinoin
steroids
MakeupAddiction
muacjdiscussion
AskWomen
SkincareAddictionUK
beautytalkph
scacjdiscussion
Accutane
ftm
amiugly
TwoXChromosomes
Rosacea
AsianBeautyAdvice
AsianBeautyRehab
PCOS
PanPorn
Skincare_Addiction
bipolar
AusSkincare
Dermatology
Makeup
pics
askgaybros
u_Vanessa35Kin
MakeupRehab
Steroidsourcetalk
TheGirlSurvivalGuide
abdiscuss

sex
traaaaaaannnnnnnnnns
transpositive
trollfitness
twentyonepilots
xxfitness
RedditLaqueristas
BeautyBoxes
RedditLaqueristas
muacjdiscussion
femalefashionadvice
RandomActsOfPolish
malepolish
MakeupAddiction
MakeupRehab
NailPolishDiscussion
Nails
lacqueristas
BabyBumps
MUAontheCheap
MakeupAddictionCanada
MtF
Nailartgifs
TheGirlSurvivalGuide
TrollXChromosomes
blogsnark
makeupexchange
makeupflatlays
PanPorn
SkincareAddiction
AsianBeauty
BeautyBoxes
Skincare_Addiction
muacjdiscussion
MakeupRehab
SkincareAddiction
Foodforthought
Indiemakeupandmore
MUWs
SkincareFlatlays
TheGirlSurvivalGuide
BeautyGuruChatter
MakeupAddiction
muacjdiscussion
MakeupAddiction
BeautyBoxes
Makeup
ParisComments
BeautyBoxes
SkincareAddiction
BeautyGuruChatter
MUAontheCheap
makeupflatlays
AsianBeauty
SkincareAddiction
makeupexchange
AskReddit
Skincare_Addiction
muacjdiscussion
scacjdiscussion
MakeupAddiction
MakeupAddicts
BeautyAddiction
MakeupRehab
makeupexchange
muacjdiscussion
AsianBeauty
AustralianMakeup
BeautyG

In [ ]:
dict_itg = {}

for i in range(0,78):
    new_gen = api.search_comments(q = itg[i], 
                                  subreddit = 'SkincareAddiction', 
                                  sort = 'asc', 
                                  fields = ['created_utc', 'score'], 
                                  size = 10)
    dict_itg[itg[i]] = list(new_gen)
    print(i)

In [187]:
df_total['On Reddit'].sum()

135

In [188]:
df_total['On Sephora'].sum()

340

In [189]:
df_total['On Allure'].sum()

237

In [190]:
df_total['On ITG'].sum()

78

In [192]:
to_investigate = ['On Reddit', 'On Allure', 'On ITG']

X = df_total[to_investigate]
y = df_total['On Sephora']

X_train, X_test, y_train, y_test = train_test_split(X, y) #stratify = y?

In [195]:
X_train.head()

On Reddit  On Allure  On ITG
135          0          0       0
341          1          1       0
58           1          0       0
405          0          1       0
409          0          1       0

In [59]:
dt.datetime.now()

datetime.datetime(2018, 10, 18, 18, 51, 33, 932599)

In [112]:
# find time difference from first original post to Sephora 

diff_time = []

for i in range(len(df_total['Reddit Posting Date'])):
    if df_total.loc[i, 'Reddit Posting Date'] == 'N/A':
        diff_time.append('N/A')
    else:
        diff_time.append((df_total.loc[i,'Reddit Posting Date']) - dt.datetime.now())

In [113]:
len(diff_time)

577

In [114]:
df_total['Time from 1st Reddit Post'] = diff_time

In [67]:
df_total['On Sephora'].value_counts()

1    340
0    237
Name: On Sephora, dtype: int64

In [ ]:
# data_dict = {}
# for j in ['SkincareAddiction', 'Sephora']:
#     for i in range(0,5):
#         new_gen = api.search_comments(q = skin_thing[i], 
#                                     subreddit = j, 
#                                     sort = 'asc', 
#                                     fields = ['created_utc'], 
#                                     size = 10)
#         data_dict[skin_thing[i]+ ' in subreddit ' + j] = list(new_gen)

In [ ]:
import datetime as dt
def get_date(created):
    return dt.datetime.fromtimestamp(created)

In [ ]:
# URL_page_2 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=2&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_3 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=3&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_4 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=4&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_5 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=5&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_6 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=6&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_7 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=7&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_8 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=8&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_9 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=9&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"
# URL_page_10 = "https://www.res-x.com/ws/r2/Resonance.aspx?appid=sephora01&tk=48738974968755173&ss=405017097206638&sg=1&pg=res18101517190053880980996&vr=5.5x&bx=true&sc=content1_rr&ev=&ei=&no=20&page=10&categoryid=&PrimaryCategoryID=&ccb=Sephora.certona&ur=https://www.sephora.com/new-beauty-products?/"

In [ ]:
# res_URL_2 = requests.get(URL_page_2, headers = {'User-agent': 'Emma York'})
# res_URL_3 = requests.get(URL_page_3, headers = {'User-agent': 'Emma York'})
# res_URL_4 = requests.get(URL_page_4, headers = {'User-agent': 'Emma York'})
# res_URL_5 = requests.get(URL_page_5, headers = {'User-agent': 'Emma York'})
# res_URL_6 = requests.get(URL_page_6, headers = {'User-agent': 'Emma York'})
# res_URL_7 = requests.get(URL_page_7, headers = {'User-agent': 'Emma York'})
# res_URL_8 = requests.get(URL_page_8, headers = {'User-agent': 'Emma York'})
# res_URL_9 = requests.get(URL_page_9, headers = {'User-agent': 'Emma York'})
# res_URL_10 = requests.get(URL_page_10, headers = {'User-agent': 'Emma York'})

In [ ]:
# html = res.text
# html_2 = res_URL_2.text
# html_3 = res_URL_3.text
# html_4 = res_URL_4.text
# html_5 = res_URL_5.text
# html_6 = res_URL_6.text
# html_7 = res_URL_7.text
# html_8 = res_URL_8.text
# html_9 = res_URL_9.text
# html_10 = res_URL_10.text

In [ ]:
# soup = BeautifulSoup(html, 'lxml')
# soup_2 = BeautifulSoup(html_2, 'lxml')
# soup_3 = BeautifulSoup(html_3, 'lxml')
# soup_4 = BeautifulSoup(html_4, 'lxml')
# soup_5 = BeautifulSoup(html_5, 'lxml')
# soup_6 = BeautifulSoup(html_6, 'lxml')
# soup_7 = BeautifulSoup(html_7, 'lxml')
# soup_8 = BeautifulSoup(html_8, 'lxml')
# soup_9 = BeautifulSoup(html_9, 'lxml')
# soup_10 = BeautifulSoup(html_10, 'lxml')